# Random Forest Models: Classification and Regression

This notebook describes how to implement Zero-Inflated Random Forest models to predict board counts at each bus stop.

 * Requiered libraries:

In [1]:
library(randomForest)
library(mlbench)
library(caret)
library(e1071)
library(dplyr)
library(tidyr)
library(readr)
library(ranger)
library(janitor)
library(rFerns)
library(ordinalForest)
library(RRF)
library(foreach)
#library(doParallel)

randomForest 4.6-14

Type rfNews() to see new features/changes/bug fixes.

Loading required package: lattice

Loading required package: ggplot2


Attaching package: ‘ggplot2’


The following object is masked from ‘package:randomForest’:

    margin


Warning message in system("timedatectl", intern = TRUE):
“running command 'timedatectl' had status 1”

Attaching package: ‘dplyr’


The following object is masked from ‘package:randomForest’:

    combine


The following objects are masked from ‘package:stats’:

    filter, lag


The following objects are masked from ‘package:base’:

    intersect, setdiff, setequal, union



Attaching package: ‘ranger’


The following object is masked from ‘package:randomForest’:

    importance



Attaching package: ‘janitor’


The following objects are masked from ‘package:stats’:

    chisq.test, fisher.test


Registered S3 method overwritten by 'RRF':
  method      from        
  plot.margin randomForest

RRF 1.9.1

Type rrfNews() to see new features/

## Zero-Inflated Random Forest Model

The proposed Zero-Inflated Random Forest model can be described as follows:

    * Classification: It learns a classifier to predict counts (> 0) and zero counts using Random Ferns.
    * Regression: It takes the *predicted counts* data to learn a regression model for these counts using Random Forest.
    
The function (`RF_Ferns_and_Ranger()`) runs the Zero-Inflated Random Forest model. It requires the following inputs:

    * `route_id == rt`.
    * `direction_id == di`.
    * `stop_id == st`.
    * `part == part` (Pre or port-lockdown dataset).
    
 *Note: The input paramters defined the file paths to run the models. If the data structure is organized in a different way, the input parameters or the paths must be change.*
    
Then, it returns a Zero-Inflated Random Forest model saved as `*.rds`. Also, a chart with the test data with the model predictions saved as `*.csv`. The test RMSE can be calculated from the this chart.

Notice that we are not reporting the train RMSE since the random forest based models are trained individually using different metrics: misclassification rate and RMSE for classification and regression respectively.

In [2]:
RF_Ferns_and_Ranger <- function(rt, di, st, part){
    
    library(randomForest)
    library(mlbench)
    library(caret)
    library(e1071)
    library(dplyr)
    library(tidyr)
    library(readr)
    library(ranger)
    library(janitor)
    library(rFerns)
    library(ordinalForest)
    library(RRF)
    library(foreach)
    #library(doParallel)
    
    path = paste0('data', '/', 'jmartinez', '/', 'Data_for_RF_Models', '/', 'Board_Counts', '/',
                  paste('route', rt, sep = '_'), '/', paste('direction', di, sep = ''), '/',
                  paste('bus_stop', st, sep = '_'), '/')
    
    if(part == 'pre'){
        file_path_train = paste(path, 'pre_lock_train_data.csv', sep = '/')
        file_path_test = paste(path, 'pre_lock_test_data.csv', sep = '/')
        
        board_train = read_csv(file_path_train)
        board_test = read_csv(file_path_test)
        
        board_train$month = factor(board_train$month)
        board_train$service_kind = factor(board_train$service_kind)
        board_train$hour = factor(board_train$hour)

        board_test$month = factor(board_test$month)
        board_test$service_kind = factor(board_test$service_kind)
        board_test$hour = factor(board_test$hour)
    }
    else if(part == 'post'){
        
        file_path_train = paste(path, 'post_lock_train_data.csv', sep = '/')
        file_path_test = paste(path, 'post_lock_test_data.csv', sep = '/')
        
        board_train = read_csv(file_path_train)
        board_test = read_csv(file_path_test)
        
        board_train$month = factor(board_train$month)
        board_train$service_kind = factor(board_train$service_kind)
        board_train$hour = factor(board_train$hour)

        board_test$month = factor(board_test$month)
        board_test$service_kind = factor(board_test$service_kind)
        board_test$hour = factor(board_test$hour)
    }
    else{
        file_path_train = paste(path, 'train_data.csv', sep = '/')
        file_path_test = paste(path, 'test_data.csv', sep = '/')
        
        board_train = read_csv(file_path_train)
        board_test = read_csv(file_path_test)
        
        board_train$month = factor(board_train$month)
        board_train$service_kind = factor(board_train$service_kind)
        board_train$hour = factor(board_train$hour)

        board_test$month = factor(board_test$month)
        board_test$service_kind = factor(board_test$service_kind)
        board_test$hour = factor(board_test$hour)
    }
    
    train_month_levels = length(levels(board_train$month))
    train_service_kind_levels = length(levels(board_train$service_kind))
    train_hour_levels = length(levels(board_train$hour))    
    
    board_test = board_test %>%
        filter(hour %in% intersect(unique(board_test$hour), unique(board_train$hour)))
    
    if(train_month_levels > 1){
        if(train_service_kind_levels > 1){
            if(train_hour_levels > 1){
                board_train = board_train
                board_test = board_test 
            }
            else{
                board_train = board_train[, -which(names(board_train) == 'hour')]
                board_test = board_test[, -which(names(board_test) == 'hour')]
            }
        }
        else{
            if(train_hour_levels > 1){
                
                board_train = board_train[, -which(names(board_train) == 'service_kind')]
                board_test = board_test[, -which(names(board_test) == 'service_kind')]
            }
            else{
                board_train = board_train[, -which(names(board_train) == c('service_kind', 'hour'))]
                board_test = board_test[, -which(names(board_test) == c('service_kind', 'hour'))]
            }
        }
    }
    else{
        if(train_service_kind_levels > 1){
            if(train_hour_levels > 1){
                board_train = board_train[, -which(names(board_train) == 'month')]
                board_test = board_test[, -which(names(board_test) == 'month')]
            }
            else{
                board_train = board_train[, -which(names(board_train) %in% c('month', 'hour'))]
                board_test = board_test[, -which(names(board_test) %in% c('month', 'hour'))]
            }
        }
        else{
            if(train_hour_levels > 1){
                board_train = board_train[, -which(names(board_train) == c('month', 'service_kind'))]
                board_test = board_test[, -which(names(board_test) == c('month', 'service_kind'))]
            }
            else{
                board_train = board_train[, -which(names(board_train) == c('month', 'service_kind', 'hour'))]
                board_test = board_test[, -which(names(board_test) == c('month', 'service_kind', 'hour'))]
            }
        }
    }
    
    board_train = remove_empty(board_train, which = c('cols'), quiet = TRUE)
    board_test = remove_empty(board_test, which = c('cols'), quiet = TRUE)
    
    train_board_counts = unique(board_train$board_count)
    test_board_counts = unique(board_test$board_count)
    
    n_row_train = nrow(board_train)
    
    if(n_row_train < 60){
        
        return('Insufficient data for analysis!')
    }
    else if(n_row_train >= 60){
        
        if(length(train_board_counts) > 1){
            y_clf_train = board_train$board_count
            y_clf_train = factor(if_else(y_clf_train == 0, 0, 1))
            
            y_clf_test = board_test$board_count
            y_clf_test = factor(if_else(y_clf_test == 0, 0, 1))
            
            Board_train_clf <- data.frame(cbind(y_clf_train, board_train[, -c(1)]))
            Board_test_clf <- data.frame(cbind(y_clf_test, board_test[, -c(1)]))
            
            #---------------------------------------------------------------------------------
            # Training characteristics for model tuning:
            #---------------------------------------------------------------------------------
            
            control <- trainControl(method = 'repeatedcv', 
                                    number = 5, 
                                    repeats = 2,
                                    search = 'random')
        
            #---------------------------------------------------------------------------------
            # Classification using Random Ferns:
            #---------------------------------------------------------------------------------
        
            set.seed(1)
            rf_random <- train(y_clf_train ~ .,
                               data = Board_train_clf,
                               method = 'rFerns',
                               metric = 'Accuracy',
                               tuneLength  = 20, 
                               trControl = control)
            
            RF_Ferns <- print(rf_random)
            
            rf_random_pred <- predict(rf_random, newdata = Board_test_clf)
            
            rf_random_conf_mat <- confusionMatrix(y_clf_test, rf_random_pred)
            rf_random_conf_mat <- data.frame(rf_random_conf_mat[4])
            colnames(rf_random_conf_mat) <- c('Value')
            
            # Index for regression data:
            
            index_for_reg <- which(rf_random_pred == '1', arr.ind = T)
            #---------------------------------------------------------------------------------
            # Regression Model using Ranger:
            
                        
            set.seed(1)
            rf_reg_ranger <- train(board_count ~ .,
                                   data = (board_train %>% filter(board_count > 0)),
                                   method = 'ranger',
                                   metric = 'RMSE',
                                   tuneLength  = 20, 
                                   trControl = control)
            
            RF_Ranger <- print(rf_reg_ranger)
                
            #----------------------------------------------------------------------------------
            # Validation:
            
            Board_Test_Val = board_test
            nrow_test = (1:nrow(board_test))
            
            Board_Test_Val$index = nrow_test
            Board_test_reg = Board_Test_Val[index_for_reg, ]
            
            rf_reg_ranger_pred <- predict(rf_reg_ranger, newdata = Board_test_reg)
            Board_test_reg$Ranger_Pred = rf_reg_ranger_pred
            
            Board_Test_Val = left_join(Board_Test_Val, Board_test_reg, by = 'index')
            
            Board_Test_Val = Board_Test_Val %>%
                mutate(RF_Pred = if_else(is.na(Ranger_Pred) == T, 0, Ranger_Pred))
            
            board_test$RF_Pred = Board_Test_Val$RF_Pred
                
            RF_test_RMSE = sqrt(mean((board_test$board_count - board_test$RF_Pred)^{2}))
            
            if(part == 'pre'){
                file_path_clf = paste(path, 'pre_lock_RF_Fern.txt', sep = '/')
                file_path_clf_conf_mat = paste(path, 'pre_Conf_Mat_RF_Fern.csv', sep = '/')
                
                file_path_reg = paste(path, 'pre_lock_RF_Reg.txt', sep = '/')
                file_path_RF_Chart = paste(path, 'pre_RF_Chart.csv', sep = '/')
                
                final_clf_model = paste(path, 'Pre_Random_Ferns_model.rds')
                final_reg_model = paste(path, 'Pre_Random_Forest_RANGER_model.rds')
                
                write.table(RF_Ferns, file_path_clf)
                write.csv(rf_random_conf_mat, file_path_clf_conf_mat)
                
                write.table(RF_Ranger, file_path_reg)
                write.csv(board_test, file_path_RF_Chart)
                
                saveRDS(rf_random, final_clf_model)
                saveRDS(rf_reg_ranger, final_reg_model)
                
            }
            else if(part == 'post'){
                
                file_path_clf = paste(path, 'post_lock_RF_Fern.txt', sep = '/')
                file_path_clf_conf_mat = paste(path, 'post_Conf_Mat_RF_Fern.csv', sep = '/')
                
                file_path_reg = paste(path, 'post_lock_RF_Reg.txt', sep = '/')
                file_path_RF_Chart = paste(path, 'post_RF_Chart.csv', sep = '/')
                
                final_clf_model = paste(path, 'Post_Random_Ferns_model.rds')
                final_reg_model = paste(path, 'Post_Random_Forest_RANGER_model.rds')
                
                write.table(RF_Ferns, file_path_clf)
                write.csv(rf_random_conf_mat, file_path_clf_conf_mat)
                
                write.table(RF_Ranger, file_path_reg)
                write.csv(board_test, file_path_RF_Chart)
                
                saveRDS(rf_random, final_clf_model)
                saveRDS(rf_reg_ranger, final_reg_model)
            }
            else{
                file_path_clf = paste(path, 'RF_Fern.txt', sep = '/')
                file_path_clf_conf_mat = paste(path, 'Conf_Mat_RF_Fern.csv', sep = '/')
                
                file_path_reg = paste(path, 'RF_Reg.txt', sep = '/')
                file_path_RF_Chart = paste(path, 'pre_RF_Chart.csv', sep = '/')
                
                final_clf_model = paste(path, 'Random_Ferns_model.rds')
                final_reg_model = paste(path, 'Random_Forest_RANGER_model.rds')
                
                write.table(RF_Ferns, file_path_clf)
                write.csv(rf_random_conf_mat, file_path_clf_conf_mat)
                
                write.table(RF_Ranger, file_path_reg)
                write.csv(board_test, file_path_RF_Chart)
                
                saveRDS(rf_random, final_clf_model)
                saveRDS(rf_reg_ranger, final_reg_model)
            }
            
            return('Done!')
            
        }
        else{
        
        return('This bus stop does not have variability in the response variable.')
            
        }    
    }    
}

## Vanilla Random Forest

The function (`vanilla_rf()`) runs Random Forest regression model considering the following inputs:

    * `route_id == rt`.
    * `direction_id == di`.
    * `stop_id == st`.
    * `part == part` (Pre or port-lockdown dataset).
    
 *Note: The input paramters defined the file paths to run the models. If the data structure is organized in a different way, the input parameters or the paths must be change.*
    
Then, it returns a Random Forest (Ranger) model saved as `*.rds`. Also, a chart with the test data with the model predictions saved as `*.csv`, and a performance file `(*.csv)` with both the train and test RMSEs.

In [64]:
vanilla_rf <- function(rt, di, st, part){
    
    library(randomForest)
    library(mlbench)
    library(caret)
    library(e1071)
    library(dplyr)
    library(tidyr)
    library(readr)
    library(ranger)
    library(janitor)
    library(rFerns)
    library(ordinalForest)
    library(RRF)
    library(foreach)
    #library(doParallel)
    
    path = paste0('data', '/', 'jmartinez', '/', 'Data_for_RF_Models', '/', 'Board_Counts', '/',
                  paste('route', rt, sep = '_'), '/', paste('direction', di, sep = ''), '/',
                  paste('bus_stop', st, sep = '_'), '/')
    
    if(part == 'pre'){
        file_path_train = paste(path, 'pre_lock_train_data.csv', sep = '/')
        file_path_test = paste(path, 'pre_lock_test_data.csv', sep = '/')
        
        board_train = read_csv(file_path_train)
        board_test = read_csv(file_path_test)
        
        board_train$month = factor(board_train$month)
        board_train$service_kind = factor(board_train$service_kind)
        board_train$hour = factor(board_train$hour)

        board_test$month = factor(board_test$month)
        board_test$service_kind = factor(board_test$service_kind)
        board_test$hour = factor(board_test$hour)
    }
    else if(part == 'post'){
        
        file_path_train = paste(path, 'post_lock_train_data.csv', sep = '/')
        file_path_test = paste(path, 'post_lock_test_data.csv', sep = '/')
        
        board_train = read_csv(file_path_train)
        board_test = read_csv(file_path_test)
        
        board_train$month = factor(board_train$month)
        board_train$service_kind = factor(board_train$service_kind)
        board_train$hour = factor(board_train$hour)

        board_test$month = factor(board_test$month)
        board_test$service_kind = factor(board_test$service_kind)
        board_test$hour = factor(board_test$hour)
    }
    else{
        file_path_train = paste(path, 'train_data.csv', sep = '/')
        file_path_test = paste(path, 'test_data.csv', sep = '/')
        
        board_train = read_csv(file_path_train)
        board_test = read_csv(file_path_test)
        
        board_train$month = factor(board_train$month)
        board_train$service_kind = factor(board_train$service_kind)
        board_train$hour = factor(board_train$hour)

        board_test$month = factor(board_test$month)
        board_test$service_kind = factor(board_test$service_kind)
        board_test$hour = factor(board_test$hour)
    }
    
    train_month_levels = length(levels(board_train$month))
    train_service_kind_levels = length(levels(board_train$service_kind))
    train_hour_levels = length(levels(board_train$hour))    
    
    board_test = board_test %>%
        filter(hour %in% intersect(unique(board_test$hour), unique(board_train$hour)))
    
    if(train_month_levels > 1){
        if(train_service_kind_levels > 1){
            if(train_hour_levels > 1){
                board_train = board_train
                board_test = board_test 
            }
            else{
                board_train = board_train[, -which(names(board_train) == 'hour')]
                board_test = board_test[, -which(names(board_test) == 'hour')]
            }
        }
        else{
            if(train_hour_levels > 1){
                
                board_train = board_train[, -which(names(board_train) == 'service_kind')]
                board_test = board_test[, -which(names(board_test) == 'service_kind')]
            }
            else{
                board_train = board_train[, -which(names(board_train) == c('service_kind', 'hour'))]
                board_test = board_test[, -which(names(board_test) == c('service_kind', 'hour'))]
            }
        }
    }
    else{
        if(train_service_kind_levels > 1){
            if(train_hour_levels > 1){
                board_train = board_train[, -which(names(board_train) == 'month')]
                board_test = board_test[, -which(names(board_test) == 'month')]
            }
            else{
                board_train = board_train[, -which(names(board_train) %in% c('month', 'hour'))]
                board_test = board_test[, -which(names(board_test) %in% c('month', 'hour'))]
            }
        }
        else{
            if(train_hour_levels > 1){
                board_train = board_train[, -which(names(board_train) == c('month', 'service_kind'))]
                board_test = board_test[, -which(names(board_test) == c('month', 'service_kind'))]
            }
            else{
                board_train = board_train[, -which(names(board_train) == c('month', 'service_kind', 'hour'))]
                board_test = board_test[, -which(names(board_test) == c('month', 'service_kind', 'hour'))]
            }
        }
    }
    
    board_train = remove_empty(board_train, which = c('cols'), quiet = TRUE)
    board_test = remove_empty(board_test, which = c('cols'), quiet = TRUE)
    
    train_board_counts = unique(board_train$board_count)
    test_board_counts = unique(board_test$board_count)
    
    n_row_train = nrow(board_train)
    
    if(n_row_train < 60){
        
        return('Insufficient data for analysis!')
    }
    else if(n_row_train >= 60){
        
        #---------------------------------------------------------------------------------
        # Training characteristics for model tuning:
        #---------------------------------------------------------------------------------
            
        control <- trainControl(method = 'repeatedcv', 
                                number = 5, 
                                repeats = 2,
                                search = 'random')
        
        #---------------------------------------------------------------------------------
        # Classification using Random Ferns:
        #---------------------------------------------------------------------------------         
                        
        set.seed(1)
        rf <- train(board_count ~ .,
                    data = board_train,
                    method = 'ranger',
                    metric = 'RMSE',
                    tuneLength  = 20, 
                    trControl = control)
            
        RF_Vanilla <- print(rf)
        
        #----------------------------------------------------------------------------------
        # Validation:
                     
        rf_vanilla_pred <- predict(rf, newdata = board_test)
        board_test$RF_Vanilla_Pred = rf_vanilla_pred
                          
        RF_train_RMSE = rf$results$RMSE[1]
        RF_test_RMSE = sqrt(mean((board_test$board_count - board_test$RF_Vanilla_Pred)^{2}))
        
        Performance = data.frame('Train' = RF_train_RMSE, 'Test'= RF_test_RMSE)
            
        if(part == 'pre'){
                            
            file_path_reg = paste(path, 'pre_lock_RF_Vanilla.txt', sep = '/')
            file_path_RF_Chart = paste(path, 'pre_RF_Vanilla_Chart.csv', sep = '/')
            file_Performance_name = paste(path, 'pre_RF_Vanilla_Performance.csv', sep = '/')
                
            final_vanilla_model = paste(path, 'Pre_RF_Vanilla_model.rds')
            
            write.csv(Performance, file_Performance_name)
            write.table(RF_Vanilla, file_path_reg)
            write.csv(board_test, file_path_RF_Chart)
                
            saveRDS(rf, final_vanilla_model)
            
                
        }
        else if(part == 'post'){
                          
            file_path_reg = paste(path, 'post_lock_RF_Vanilla.txt', sep = '/')
            file_path_RF_Chart = paste(path, 'post_RF_Vanilla_Chart.csv', sep = '/')
            file_Performance_name = paste(path, 'post_RF_Vanilla_Performance.csv', sep = '/')
                
            final_vanilla_model = paste(path, 'Post_RF_Vanilla_model.rds')
                
            write.csv(Performance, file_Performance_name)
            write.table(RF_Vanilla, file_path_reg)
            write.csv(board_test, file_path_RF_Chart)
                
            saveRDS(rf, final_vanilla_model)
        }
        else{
            
            file_path_reg = paste(path, 'RF_Vanilla.txt', sep = '/')
            file_path_RF_Chart = paste(path, 'RF_Vanilla_Chart.csv', sep = '/')
            write.csv(Performance, file_Performance_name)
                
            final_vanilla_model = paste(path, 'RF_Vanilla_model.rds')
            
            write.csv(Performance, file_Performance_name)
            write.table(RF_Vanilla, file_path_reg)
            write.csv(board_test, file_path_RF_Chart)
                
            saveRDS(rf, final_vanilla_model)
        }
            
        return('Done!')
            
    }
    else{
        
    return('This bus stop does not have variability in the response variable.')
            
    }    
    
}

### Example 1: 

We can assess the function using the data from `route_id == '1`, `direction_id == '0'`, `stop_id == 287`, and pre-lockown data.

In [26]:
RF_Ferns_and_Ranger('1', '0', '287', 'pre')


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

180 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 143, 145, 144, 144, 144, 144, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9247490  0.7853098
   2     0.8914908  0.7190953
   3     0.8944230  0.7295618
   5     0.8914865  0.7185389
   6     0.8802960  0.6966475
   7     0.8803754  0.6896168
   9     0.8636293  0.6619662
  10     0.8580738  0.6512519
  11     0.8608516  0.6566090
  13     0.8413278  0.6170465
  14     0.8413278  0.6167441
  15     0.8413278  0.6136446

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

31 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 25, 25, 25, 24, 25, 24, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  split

[1] "Done!"

### Example 2:

Similarly, we can assess the function using the data from `route_id == '1`, `direction_id == '0'`, `stop_id == 287`, and pre-lockown data.

In [34]:
vanilla_rf('1', '0', '287', 'pre')


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

180 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 144, 144, 144, 144, 144, 144, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared   MAE      
   1              6    extratrees  0.8187776  0.1374368  0.4650773
   1             25    maxstat     0.7291883  0.2686570  0.3666066
   2              8    maxstat     0.7393259  0.2402884  0.4210523
   2             12    extratrees  0.8189573  0.1547768  0.4490979
   5              6    maxstat     0.7418645  0.2291773  0.4378397
   5             12    extratrees  0.7967272  0.1904981  0.4398366
   5             25    extratrees  0.8016534  0.1998440  0.4265870
   7             10    variance    0.7965188  0.1925592  0.4338501
   7             15    extratrees  0.7798713  0.2236923  0.4297727
   9             20    extratrees  0.7705565  0.2395065  0.4188310
   9             25    variance    0.806

[1] "Done!"

# For-Loop by route and direction

We can use a `for`-loop to iterate this process by extacting the `stop_id`s per `route_id` and `direction_id`.

In [4]:
Pre_lock = read_csv('data/jmartinez/Transit_Data/Pre_lock.csv')


── Column specification ────────────────────────────────────────────────────────
cols(
  .default = col_double(),
  scheduled_arrival_time = col_datetime(format = ""),
  actual_arrival_time = col_datetime(format = ""),
  direction_desc = col_character(),
  service_period = col_character(),
  date = col_date(format = ""),
  scheduled_datetime = col_datetime(format = ""),
  actual_arrival_datetime = col_datetime(format = ""),
  trip_start_time = col_datetime(format = ""),
  trip_date = col_date(format = ""),
  service_kind = col_character()
)
ℹ Use `spec()` for the full column specifications.




In [5]:
Post_lock = read_csv('data/jmartinez/Transit_Data/Post_lock.csv')


── Column specification ────────────────────────────────────────────────────────
cols(
  .default = col_double(),
  scheduled_arrival_time = col_datetime(format = ""),
  actual_arrival_time = col_datetime(format = ""),
  direction_desc = col_character(),
  service_period = col_character(),
  date = col_date(format = ""),
  scheduled_datetime = col_datetime(format = ""),
  actual_arrival_datetime = col_datetime(format = ""),
  trip_start_time = col_datetime(format = ""),
  trip_date = col_date(format = ""),
  service_kind = col_character()
)
ℹ Use `spec()` for the full column specifications.




In [6]:
head(Pre_lock)

trip_id scheduled_arrival_time actual_arrival_time stop_id stop_sequence
1 132994  1900-01-01 04:55:00    1900-01-01 04:52:00 1351    1            
2 132994  1900-01-01 04:55:41    1900-01-01 04:56:00   12    2            
3 132994  1900-01-01 04:56:20    1900-01-01 04:57:00 1555    3            
4 132994  1900-01-01 04:56:35    1900-01-01 04:57:00 1579    4            
5 132994  1900-01-01 04:57:22    1900-01-01 04:57:00 1354    5            
6 132994  1900-01-01 04:57:35    1900-01-01 04:57:00 1353    6            
  stop_lat stop_lon  route_id direction_id board_count ⋯
1 35.05266 -85.30972 1        0            1           ⋯
2 35.05070 -85.30953 1        0            0           ⋯
3 35.04883 -85.30955 1        0            0           ⋯
4 35.04812 -85.30955 1        0            0           ⋯
5 35.04598 -85.30952 1        0            0           ⋯
6 35.04538 -85.30945 1        0            0           ⋯
  actual_arrival_datetime trip_start_time     day_of_week trip_date  hour year
1 2019-01-02 04:52:00     1900-01-01 04:55:00 2           2019-01-02 4    2019
2 2019-01-02 04:56:00     1900-01-01 04:55:00 2           2019-01-02 4    2019
3 2019-01-02 04:57:00     1900-01-01 04:55:00 2           2019-01-02 4    2019
4 2019-01-02 04:57:00     1900-01-01 04:55:00 2           2019-01-02 4    2019
5 2019-01-02 04:57:00     1900-01-01 04:55:00 2           2019-01-02 4    2019
6 2019-01-02 04:57:00     1900-01-01 04:55:00 2           2019-01-02 4    2019
  month Estimated_Temp Estimated_Precip service_kind
1 1     8.350000       0                weekday     
2 1     8.343167       0                weekday     
3 1     8.336667       0                weekday     
4 1     8.334167       0                weekday     
5 1     8.326333       0                weekday     
6 1     8.324167       0                weekday

In [7]:
dim(Pre_lock)

[1] 8602818      26

In [8]:
Pre_lock$trip_id = as.character(Pre_lock$trip_id)
Pre_lock$stop_id = as.character(Pre_lock$stop_id)
Pre_lock$route_id = as.character(Pre_lock$route_id)
Pre_lock$direction_id = as.character(Pre_lock$direction_id)
Pre_lock$hour = factor(Pre_lock$hour)
Pre_lock$month = factor(Pre_lock$month)

In [9]:
Post_lock$trip_id = as.character(Post_lock$trip_id)
Post_lock$stop_id = as.character(Post_lock$stop_id)
Post_lock$route_id = as.character(Post_lock$route_id)
Post_lock$direction_id = as.character(Post_lock$direction_id)
Post_lock$hour = factor(Post_lock$hour)
Post_lock$month = factor(Post_lock$month)

## Extracting the `stop_id`s by route for both directions

### Pre-lockdown

In [10]:
bus_stops_r1_dir0_pre = Pre_lock %>%  
    filter(route_id == '1', direction_id == '0') %>%
    pull(stop_id)

bus_stops_r1_dir0_pre = unique(bus_stops_r1_dir0_pre)

bus_stops_r1_dir1_pre = Pre_lock %>%  
    filter(route_id == '1', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r1_dir1_pre = unique(bus_stops_r1_dir1_pre)

bus_stops_r4_dir0_pre = Pre_lock %>%  
    filter(route_id == '4', direction_id == '0') %>%
    pull(stop_id)

bus_stops_r4_dir0_pre = unique(bus_stops_r4_dir0_pre)

bus_stops_r4_dir1_pre = Pre_lock %>%  
    filter(route_id == '4', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r4_dir1_pre = unique(bus_stops_r4_dir1_pre)

bus_stops_r9_dir0_pre = Pre_lock %>%  
    filter(route_id == '9', direction_id == '0') %>%
    pull(stop_id)

bus_stops_r9_dir0_pre = unique(bus_stops_r9_dir0_pre)

bus_stops_r9_dir1_pre = Pre_lock %>%  
    filter(route_id == '9', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r9_dir1_pre = unique(bus_stops_r9_dir1_pre)

### Post-lockdown

In [11]:
bus_stops_r1_dir0_post = Post_lock %>%  
    filter(route_id == '1', direction_id == '0') %>%
    pull(stop_id)

bus_stops_r1_dir0_post = unique(bus_stops_r1_dir0_post)

bus_stops_r1_dir1_post = Post_lock %>%  
    filter(route_id == '1', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r1_dir1_post = unique(bus_stops_r1_dir1_post)

bus_stops_r4_dir0_post = Post_lock %>%  
    filter(route_id == '4', direction_id == '0') %>%
    pull(stop_id)

bus_stops_r4_dir0_post = unique(bus_stops_r4_dir0_post)

bus_stops_r4_dir1_post = Post_lock %>%  
    filter(route_id == '4', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r4_dir1_post = unique(bus_stops_r4_dir1_post)

bus_stops_r9_dir0_post = Post_lock %>%  
    filter(route_id == '9', direction_id == '0') %>%
    pull(stop_id)

bus_stops_r9_dir0_post = unique(bus_stops_r9_dir0_post)

bus_stops_r9_dir1_post = Post_lock %>%  
    filter(route_id == '9', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r9_dir1_post = unique(bus_stops_r9_dir1_post)

# Results

## Route 1

### Direction 0

#### Pre-lockdown

In [44]:
bus_stops_r1_dir0_pre

[1] "1351" "12"   "1555" "1579" "1354" "1353" "17"   "742"  "18"   "19"  
[11] "1557" "1357" "21"   "22"   "23"   "24"   "25"   "26"   "27"   "28"  
[21] "354"  "505"  "784"  "283"  "284"  "285"  "713"  "286"  "287"  "95"  
[31] "44"

In [15]:
# 25, 284, 285, 95, 44

In [43]:
for(i in bus_stops_r1_dir0_pre[1:length(bus_stops_r1_dir0_pre)]){
    print(i)
    RF_Ferns_and_Ranger('1', '0', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "44"


ERROR: Error: 'data/jmartinez/Data_for_RF_Models/Board_Counts/route_1/direction0/bus_stop_44//pre_lock_train_data.csv' does not exist in current working directory ('/home/jmartinez').


### Vanilla Random Forest

In [46]:
Bus_stops_r1_dir0_pre = bus_stops_r1_dir0_pre[-which(bus_stops_r1_dir0_pre %in% c('25',  '284', '285', '95', '44', '713', '286'), arr.ind = T)]
Bus_stops_r1_dir0_pre

[1] "1351" "12"   "1555" "1579" "1354" "1353" "17"   "742"  "18"   "19"  
[11] "1557" "1357" "21"   "22"   "23"   "24"   "26"   "27"   "28"   "354" 
[21] "505"  "784"  "283"  "287"

In [ ]:
# 713, 286

In [47]:
for(i in Bus_stops_r1_dir0_pre){
    print(i)
    vanilla_rf('1', '0', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "1351"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

1198 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 959, 959, 959, 957, 958, 959, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared     MAE     
   1             15    extratrees  1.830707  0.004392122  1.412792
   1             20    maxstat     1.537916  0.094319430  1.151440
   2             18    variance    1.829009  0.005222901  1.409096
   2             33    extratrees  1.833474  0.005074083  1.409872
   5              2    maxstat     1.599829  0.095050261  1.228829
   5              6    variance    1.737439  0.010466686  1.337911
   5             14    extratrees  1.785052  0.007049537  1.372457
   7              6    maxstat     1.567191  0.099036257  1.195414
   7             25    extratrees  1.780797  0.008583438  1.364188
   9             24    variance    1.777448  0.009478839  1.364984
   9             25    variance    1.7


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

2411 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1929, 1929, 1930, 1928, 1928, 1930, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE     
   1             15    extratrees  1.997005  0.07295139  1.511251
   1             20    maxstat     1.819936  0.16821380  1.370690
   2             18    variance    1.998135  0.07315344  1.510001
   2             33    extratrees  1.996553  0.07399087  1.507155
   5              2    maxstat     1.960985  0.12372130  1.502088
   5              6    variance    1.953379  0.08670280  1.483042
   5             14    extratrees  1.985429  0.07663686  1.502253
   7              6    maxstat     1.880526  0.15598289  1.431452
   7             25    extratrees  1.983746  0.07823680  1.498056
   9             24    variance    1.985250  0.07791534  1.498993
   9             25    variance    1.985432

...

Random Forest 

142 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 114, 114, 114, 113, 113, 114, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1              6    extratrees  0.6696894  0.03167896  0.3230701
   1             25    maxstat     0.5747830  0.19145437  0.2510865
   2              8    maxstat     0.5608638  0.13566162  0.2841982
   2             12    extratrees  0.6772797  0.04459757  0.3158545
   5              6    maxstat     0.5567555  0.13300023  0.2919292
   5             12    extratrees  0.6484052  0.05798438  0.3069546
   5             25    extratrees  0.6561709  0.06020957  0.3015538
   7             10    variance    0.6481343  0.07236659  0.3020759
   7             15    extratrees  0.6332132  0.06836754  0.3039824
   9             20    extratrees  0.6223854  0.08529756  0.2990287
   9             25    varian


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

130 samples
  6 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 104, 104, 104, 104, 104, 104, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared   MAE       
   1             10    extratrees  0.3243519  0.7441995  0.07789714
   1             12    extratrees  0.3216401  0.7462146  0.07690295
   2             15    maxstat     0.3420838  0.4848142  0.10539303
   2             24    extratrees  0.2881466  0.7909656  0.06469154
   5             12    maxstat     0.3478128  0.4199303  0.11161106
   5             23    maxstat     0.3401823  0.4009610  0.09530329
   7             10    extratrees  0.3038145  0.7586649  0.08152354
   7             20    extratrees  0.2757878  0.8044867  0.06624300
   9              6    maxstat     0.3651904  0.4353432  0.12743989
   9             20    extratrees  0.2715988  0.8061823  0.06818357
  10             10    varian


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

180 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 144, 144, 144, 144, 144, 144, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared   MAE      
   1              6    extratrees  0.8187776  0.1374368  0.4650773
   1             25    maxstat     0.7291883  0.2686570  0.3666066
   2              8    maxstat     0.7393259  0.2402884  0.4210523
   2             12    extratrees  0.8189573  0.1547768  0.4490979
   5              6    maxstat     0.7418645  0.2291773  0.4378397
   5             12    extratrees  0.7967272  0.1904981  0.4398366
   5             25    extratrees  0.8016534  0.1998440  0.4265870
   7             10    variance    0.7965188  0.1925592  0.4338501
   7             15    extratrees  0.7798713  0.2236923  0.4297727
   9             20    extratrees  0.7705565  0.2395065  0.4188310
   9             25    variance    0.806

#### Post-lockdown

In [43]:
bus_stops_r1_dir0_post

[1] "354"  "505"  "784"  "283"  "284"  "285"  "713"  "286"  "287"  "1351"
[11] "12"   "1555" "1579" "1354" "1353" "17"   "742"  "18"   "19"   "1557"
[21] "1357" "21"   "22"   "23"   "24"   "25"   "26"   "27"   "28"   "95"

In [ ]:
# 95

In [45]:
for(i in bus_stops_r1_dir0_post[1:length(bus_stops_r1_dir0_post)]){
    print(i)
    RF_Ferns_and_Ranger('1', '0', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "354"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "784"


...

Random Ferns 

193 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 154, 155, 154, 155, 154, 154, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9247638  0.8276084
   2     0.9143050  0.7925950
   3     0.9139676  0.7957706
   5     0.9195682  0.7988092
   6     0.9143050  0.7895584
   7     0.9066802  0.7791084
   9     0.8858974  0.7298974
  10     0.8727395  0.7033432
  11     0.8962888  0.7447449
  13     0.8574224  0.6721458
  14     0.8625506  0.6810785
  15     0.8522942  0.6594606

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

43 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 35, 35, 34, 34, 34, 33, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  split


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

154 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 123, 123, 124, 123, 123, 123, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9607527  0.9118657
   2     0.9870968  0.9701491
   3     0.9707527  0.9337936
   5     0.9643011  0.9178214
   6     0.9707527  0.9329803
   7     0.9707527  0.9329803
   9     0.9610753  0.9107089
  10     0.9478495  0.8833739
  11     0.9511828  0.8895072
  13     0.9447312  0.8757073
  14     0.9317204  0.8474115
  15     0.9318280  0.8493090

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 2.
Random Forest 

44 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 36, 36, 34, 35, 35, 35, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  split


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message:
“Unknown or uninitialised column: `board_count`.”


[1] "Done!"
[1] "_/|_/|_"


### Vanilla Random Forest

In [48]:
Bus_stops_r1_dir0_post =  bus_stops_r1_dir0_post[-which(bus_stops_r1_dir0_post == '95', arr.ind = T)]
Bus_stops_r1_dir0_post

[1] "354"  "505"  "784"  "283"  "284"  "285"  "713"  "286"  "287"  "1351"
[11] "12"   "1555" "1579" "1354" "1353" "17"   "742"  "18"   "19"   "1557"
[21] "1357" "21"   "22"   "23"   "24"   "25"   "26"   "27"   "28"

In [49]:
for(i in Bus_stops_r1_dir0_post){
    print(i)
    vanilla_rf('1', '0', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "354"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "784"


...

Random Forest 

236 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 189, 189, 189, 188, 189, 188, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1              6    extratrees  0.8290805  0.03120417  0.5279178
   1             25    maxstat     0.7311435  0.12697254  0.4540807
   2             12    extratrees  0.8453640  0.02863088  0.5270628
   2             25    maxstat     0.7324941  0.12432036  0.4548710
   5              6    extratrees  0.8142413  0.03602645  0.5213030
   5             23    maxstat     0.7323152  0.12484636  0.4558747
   5             26    extratrees  0.8336943  0.03537225  0.5183299
   7             10    variance    0.8243616  0.03938222  0.5180386
   7             15    extratrees  0.8158564  0.03841501  0.5152953
   9             12    variance    0.8173249  0.04348433  0.5132743
   9             20    extrat


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

193 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 155, 155, 154, 154, 154, 155, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1              6    extratrees  1.0293625  0.01671039  0.6319415
   1             25    maxstat     0.8564275  0.14487488  0.4977890
   2             12    extratrees  1.0519246  0.01540853  0.6354401
   2             25    maxstat     0.8566091  0.14540027  0.4977550
   5              6    extratrees  0.9963099  0.02062042  0.6170192
   5             23    maxstat     0.8555108  0.14459391  0.4993368
   5             26    extratrees  1.0261992  0.01833479  0.6177328
   7             10    variance    1.0172039  0.01948854  0.6111358
   7             15    extratrees  0.9984467  0.02083901  0.6111746
   9             12    variance    1.0045711  0.02070340  0.6000561
   9             20    extrat


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

154 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 124, 124, 123, 122, 123, 123, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1              6    extratrees  0.9227940  0.09862667  0.6361471
   1             25    maxstat     0.8241338  0.19240676  0.5179953
   2             12    extratrees  0.9420246  0.10005714  0.6339661
   2             25    maxstat     0.8225106  0.19462225  0.5177717
   5              6    extratrees  0.8910899  0.10607847  0.6221931
   5             23    maxstat     0.8207889  0.19490065  0.5189770
   5             26    extratrees  0.9252832  0.10401869  0.6183771
   7             10    variance    0.9089149  0.12336206  0.6031397
   7             15    extratrees  0.8985471  0.10903850  0.6126713
   9             12    variance    0.8990893  0.12962010  0.5925499
   9             20    extrat

## Route 1

### Direction 1

#### Pre-lockdown

In [40]:
bus_stops_r1_dir1_pre

[1] "95"   "1891" "1915" "72"   "1892" "161"  "74"   "75"   "158"  "157" 
[11] "155"  "146"  "81"   "90"   "1486" "1899" "148"  "1731" "1797" "151" 
[21] "152"  "100"  "101"  "102"  "103"  "104"  "105"  "107"  "108"  "109" 
[31] "110"  "111"  "112"  "113"  "114"  "115"  "116"  "1912" "118"  "1914"
[41] "1358" "1582" "124"  "125"  "126"  "127"  "128"  "129"  "130"  "132" 
[51] "133"  "134"  "136"  "137"  "1487" "138"  "139"  "140"  "141"  "142" 
[61] "143"  "771"  "144"  "145"  "150"  "106"  "1913" "1488" "1684" "1560"
[71] "163"  "164"  "165"  "1361" "1589" "166"  "167"  "169"  "170"  "171" 
[81] "172"  "505"  "690"  "44"

In [ ]:
# 1560, 167, 172, 505, 44

In [55]:
which(bus_stops_r1_dir1_pre == '505', arr.ind = T)

[1] 82

In [56]:
for(i in bus_stops_r1_dir1_pre[83:length(bus_stops_r1_dir1_pre)]){
    print(i)
    RF_Ferns_and_Ranger('1', '1', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "690"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "44"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




ERROR: Error: Problem with `summarise()` input `..4`.
[34mℹ[39m `..4 = mean_temp`.
[31m✖[39m object 'mean_temp' not found


In [59]:
Bus_stops_r1_dir1_pre = bus_stops_r1_dir1_pre[-which(bus_stops_r1_dir1_pre %in% c('1560', '167', '172', '505', '44', '169', '170', '171', '690'), arr.ind = T)]
Bus_stops_r1_dir1_pre

[1] "95"   "1891" "1915" "72"   "1892" "161"  "74"   "75"   "158"  "157" 
[11] "155"  "146"  "81"   "90"   "1486" "1899" "148"  "1731" "1797" "151" 
[21] "152"  "100"  "101"  "102"  "103"  "104"  "105"  "107"  "108"  "109" 
[31] "110"  "111"  "112"  "113"  "114"  "115"  "116"  "1912" "118"  "1914"
[41] "1358" "1582" "124"  "125"  "126"  "127"  "128"  "129"  "130"  "132" 
[51] "133"  "134"  "136"  "137"  "1487" "138"  "139"  "140"  "141"  "142" 
[61] "143"  "771"  "144"  "145"  "150"  "106"  "1913" "1488" "1684" "163" 
[71] "164"  "165"  "1361" "1589" "166"

In [53]:
length(Bus_stops_r1_dir1_pre)

[1] 79

In [57]:
which(Bus_stops_r1_dir1_pre == '171', arr.ind = T)

[1] 78

In [ ]:
# 169, 170, 171, 690

In [58]:
for(i in Bus_stops_r1_dir1_pre){
    print(i)
    vanilla_rf('1', '1', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "690"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




ERROR: Error in cut.default(y, breaks, include.lowest = TRUE): invalid number of intervals


#### Post-lockdown

In [57]:
bus_stops_r1_dir1_post

[1] "95"   "1891" "1915" "72"   "1892" "161"  "74"   "75"   "158"  "155" 
[11] "146"  "81"   "90"   "1486" "1899" "148"  "1731" "1797" "150"  "151" 
[21] "152"  "103"  "104"  "105"  "107"  "108"  "109"  "110"  "111"  "112" 
[31] "113"  "114"  "115"  "116"  "1912" "118"  "1914" "1358" "1582" "124" 
[41] "125"  "126"  "127"  "128"  "129"  "130"  "132"  "133"  "134"  "136" 
[51] "137"  "1487" "138"  "139"  "140"  "141"  "142"  "143"  "771"  "144" 
[61] "145"  "157"  "1913" "100"  "101"  "106"  "1488" "1684" "1560" "163" 
[71] "164"  "165"  "1361" "1589" "166"  "167"  "169"  "170"  "171"  "172" 
[81] "505"  "102"  "690"

In [ ]:
# 72, 1892, 126, 134

In [65]:
which(bus_stops_r1_dir1_post == '134', arr.ind = T)

[1] 49

In [66]:
for(i in bus_stops_r1_dir1_post[50:length(bus_stops_r1_dir1_post)]){
    print(i)
    RF_Ferns_and_Ranger('1', '1', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "136"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

125 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 100, 100, 101, 99, 100, 101, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.8213077  0.4653941
   2     0.8014615  0.4527437
   3     0.8174359  0.4932105
   5     0.8054359  0.4738444
   6     0.7931282  0.4512217
   7     0.7892821  0.4449636
   9     0.7652692  0.4122646
  10     0.7694359  0.4173070
  11     0.7614359  0.4078601
  13     0.7774359  0.4244870
  14     0.7375769  0.3634971
  15     0.7375769  0.3725373

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

14 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 11, 12, 11, 11, 11, 11, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared   MAE     
   1              9    variance    1.395111  0.6532043  1.249546
   1             15    maxstat     1.266933  0.5737307  1.156775
   2             10    extratrees  1.379764  0.5843419  1.247818
   2             25    maxstat     1.270922  0.6070070  1.156781
   3             12    maxstat     1.241897  0.5981875  1.124989
   5              1    extratrees  1.145203  0.5939774  1.038426
   5             20    extratrees  1.373652  0.5436940  1.246180
   6              6    extratrees  1.280352  0.6456323  1.160229
   7              5    extratrees  1.225431  0.5897086  1.112512
   7              5    variance    1.274118  0.6623528  1.154153
   7              6    extratrees  1.241334  0.6309863  1.127552
   9 

...

Random Ferns 

112 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 90, 89, 90, 89, 90, 90, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.8928854  0.7302112
   2     0.9015810  0.7500388
   3     0.8970356  0.7361168
   5     0.9059289  0.7539316
   6     0.8883399  0.7175554
   7     0.9013834  0.7465297
   9     0.8924901  0.7267241
  10     0.8881423  0.7163111
  11     0.8792490  0.6994052
  13     0.8790514  0.7011520
  14     0.8792490  0.7006415
  15     0.8656126  0.6735847

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 5.


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

22 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 18, 17, 18, 18, 17, 17, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared   MAE      
   1              6    extratrees  1.0607388  0.4130209  0.9184371
   1             25    maxstat     1.0053436  0.2771547  0.8455049
   2             12    extratrees  1.0815857  0.3775151  0.9186541
   2             25    maxstat     1.0062995  0.2818760  0.8427989
   5              6    extratrees  1.0348971  0.3660655  0.8952917
   5             23    maxstat     1.0048686  0.2617758  0.8466576
   5             26    extratrees  1.0817536  0.3657537  0.8877391
   7             10    variance    1.0149818  0.2781025  0.8874102
   7             15    extratrees  1.0440218  0.3472727  0.8737729
   9             12    variance    1.0025366  0.2907856  0.8754500
   9             20    extratrees  1.0197789  0.


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


### Vanilla RF

In [61]:
Bus_stops_r1_dir1_post = bus_stops_r1_dir1_post[-which(bus_stops_r1_dir1_post %in% c('72', '1892', '126', '134'), arr.ind = T)]
Bus_stops_r1_dir1_post

[1] "95"   "1891" "1915" "161"  "74"   "75"   "158"  "155"  "146"  "81"  
[11] "90"   "1486" "1899" "148"  "1731" "1797" "150"  "151"  "152"  "103" 
[21] "104"  "105"  "107"  "108"  "109"  "110"  "111"  "112"  "113"  "114" 
[31] "115"  "116"  "1912" "118"  "1914" "1358" "1582" "124"  "125"  "127" 
[41] "128"  "129"  "130"  "132"  "133"  "136"  "137"  "1487" "138"  "139" 
[51] "140"  "141"  "142"  "143"  "771"  "144"  "145"  "157"  "1913" "100" 
[61] "101"  "106"  "1488" "1684" "1560" "163"  "164"  "165"  "1361" "1589"
[71] "166"  "167"  "169"  "170"  "171"  "172"  "505"  "102"  "690"

In [62]:
length(Bus_stops_r1_dir1_post)

[1] 79

In [ ]:
# 127, 140, 144

In [70]:
which(Bus_stops_r1_dir1_post == '144', arr.ind = T)

[1] 56

In [71]:
for(i in Bus_stops_r1_dir1_post[57:79]){
    print(i)
    vanilla_rf('1', '1', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "145"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

231 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 185, 185, 185, 184, 185, 184, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE       
   1              6    extratrees  0.2367611  0.08635302  0.06041757
   1             25    maxstat     0.2035183  0.20700103  0.05430450
   2             12    extratrees  0.2424617  0.07336213  0.06061154
   2             25    maxstat     0.2014687  0.22780410  0.05367938
   5              6    extratrees  0.2248158  0.10156922  0.05826919
   5             23    maxstat     0.2008714  0.18633471  0.05412514
   5             26    extratrees  0.2351821  0.14784496  0.05874675
   7             10    variance    0.2291188  0.14021688  0.05882237
   7             15    extratrees  0.2235248  0.15264705  0.05785754
   9             12    variance    0.2226915  0.16178011  0.05828013
   9             2


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

222 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 178, 178, 178, 177, 177, 178, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE      
   1              6    extratrees  1.426612  0.03832536  0.9486273
   1             25    maxstat     1.230907  0.15639026  0.7782660
   2              8    maxstat     1.241230  0.10878936  0.8468188
   2             12    extratrees  1.446384  0.03703778  0.9496724
   5              6    maxstat     1.246593  0.10198434  0.8630639
   5             12    extratrees  1.409314  0.04256139  0.9332668
   5             25    extratrees  1.419590  0.04335443  0.9254368
   7             10    variance    1.395048  0.04545065  0.9211438
   7             15    extratrees  1.383774  0.04448952  0.9167627
   9             20    extratrees  1.372161  0.04867052  0.9071276
   9             25    variance    1.403

...

[1] "Done!"
[1] "_/|_/|_"
[1] "102"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

112 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 90, 90, 90, 89, 89, 90, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1              6    extratrees  0.8252905  0.06139689  0.4899940
   1             25    maxstat     0.6994597  0.25118789  0.3695666
   2             12    extratrees  0.8316842  0.06696787  0.4781769
   2             25    maxstat     0.6989467  0.25384211  0.3694689
   5              6    extratrees  0.7830297  0.08719920  0.4726217
   5             23    maxstat     0.6972892  0.25229278  0.3713808
   5             26    extratrees  0.8021264  0.09432720  0.4553121
   7             10    variance    0.7877324  0.10892228  0.4554171
   7             15    extratrees  0.7747468  0.10755899  0.4496574
   9             12    variance    0.7753476  0.12587870  0.4425597
   9             20    extratrees  


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


## Route 4

### Direction 0

#### Pre-lockdown

In [67]:
bus_stops_r4_dir0_pre

[1] "354"  "505"  "284"  "285"  "713"  "286"  "287"  "1351" "12"   "1555"
 [11] "1579" "1354" "1353" "17"   "742"  "805"  "806"  "807"  "1475" "1474"
 [21] "811"  "812"  "813"  "814"  "815"  "816"  "817"  "818"  "819"  "820" 
 [31] "821"  "822"  "823"  "824"  "825"  "826"  "827"  "828"  "829"  "321" 
 [41] "322"  "830"  "831"  "832"  "833"  "834"  "835"  "836"  "837"  "838" 
 [51] "839"  "840"  "841"  "842"  "843"  "844"  "845"  "846"  "848"  "849" 
 [61] "850"  "851"  "852"  "854"  "892"  "855"  "1875" "856"  "894"  "784" 
 [71] "857"  "858"  "283"  "859"  "897"  "860"  "861"  "898"  "1873" "1848"
 [81] "1849" "1850" "1819" "867"  "1877" "868"  "869"  "870"  "871"  "872" 
 [91] "873"  "874"  "875"  "876"  "877"  "879"  "880"  "881"  "882"  "883" 
[101] "884"  "885"  "886"  "887"  "888"  "889"  "890"  "891"  "1485" "1876"
[111] "1482" "1465" "1466" "1468" "1469" "1470" "1471" "1472" "1473" "1878"
[121] "18"   "19"   "1557" "1357" "21"   "22"   "23"   "24"   "25"   "900" 
[131] "901"  "902"  "903"  "1908" "905"  "1909" "907"  "908"  "1910" "1880"
[141] "1917" "1882"

In [ ]:
# 713, 286, 1877, 1469, 1472, 24, 25, 901, 902, 903, 905, 1909, 1882

In [77]:
which(bus_stops_r4_dir0_pre == '1882', arr.ind = T)

[1] 142

In [91]:
for(i in bus_stops_r4_dir0_pre[137:length(bus_stops_r4_dir0_pre)]){
    print(i)
    RF_Ferns_and_Ranger('4', '0', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "907"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "908"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1910"


...

[1] "Done!"
[1] "_/|_/|_"
[1] "1917"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1882"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




ERROR: Error: Problem with `summarise()` input `..4`.
[34mℹ[39m `..4 = mean_temp`.
[31m✖[39m object 'mean_temp' not found


### Vanilla RF

In [ ]:
# 713, 286, 1877, 1469, 1472, 24, 25, 901, 902, 903, 905, 1909, 1882

In [73]:
Bus_stops_r4_dir0_pre = bus_stops_r4_dir0_pre[-which(bus_stops_r4_dir0_pre %in% c('713', '286', '1877', '1469', '1472', '24', '25', '901', '902', '903', '905', '1909', '1882'), arr.ind = T)]
Bus_stops_r4_dir0_pre

[1] "354"  "505"  "284"  "285"  "287"  "1351" "12"   "1555" "1579" "1354"
 [11] "1353" "17"   "742"  "805"  "806"  "807"  "1475" "1474" "811"  "812" 
 [21] "813"  "814"  "815"  "816"  "817"  "818"  "819"  "820"  "821"  "822" 
 [31] "823"  "824"  "825"  "826"  "827"  "828"  "829"  "321"  "322"  "830" 
 [41] "831"  "832"  "833"  "834"  "835"  "836"  "837"  "838"  "839"  "840" 
 [51] "841"  "842"  "843"  "844"  "845"  "846"  "848"  "849"  "850"  "851" 
 [61] "852"  "854"  "892"  "855"  "1875" "856"  "894"  "784"  "857"  "858" 
 [71] "283"  "859"  "897"  "860"  "861"  "898"  "1873" "1848" "1849" "1850"
 [81] "1819" "867"  "868"  "869"  "870"  "871"  "872"  "873"  "874"  "875" 
 [91] "876"  "877"  "879"  "880"  "881"  "882"  "883"  "884"  "885"  "886" 
[101] "887"  "888"  "889"  "890"  "891"  "1485" "1876" "1482" "1465" "1466"
[111] "1468" "1470" "1471" "1473" "1878" "18"   "19"   "1557" "1357" "21"  
[121] "22"   "23"   "900"  "1908" "907"  "908"  "1910" "1880" "1917"

In [98]:
length(Bus_stops_r4_dir0_pre)

[1] 129

In [ ]:
which(Bus_stops_r4_dir0_pre == '', arr.ind = T)

In [79]:
for(i in Bus_stops_r4_dir0_pre){
    print(i)
    vanilla_rf('4', '0', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "354"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

684 samples
  6 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 547, 547, 548, 547, 547, 546, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE     
   1              6    extratrees  1.887274  0.01336409  1.499409
   1             25    variance    1.976921  0.01128565  1.568181
   2              6    extratrees  1.884040  0.01314805  1.496346
   2             12    maxstat     1.677298  0.09215306  1.308872
   5             20    extratrees  1.940236  0.01219480  1.537530
   5             23    maxstat     1.677751  0.09469678  1.305266
   5             25    maxstat     1.678873  0.09433474  1.305679
   7             10    variance    1.915801  0.01373637  1.518026
   7             15    variance    1.931869  0.01318650  1.530466
   9             20    extratrees  1.891176  0.01738962  1.493368
   9             26    extratrees  1.898966  0.0163


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

380 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 304, 304, 304, 304, 304, 305, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE      
   1              6    extratrees  1.335237  0.04620650  0.8271712
   1             25    variance    1.361794  0.05377760  0.8050155
   2              6    extratrees  1.327041  0.04890424  0.8216075
   2             12    maxstat     1.123915  0.16475419  0.6645504
   5             20    extratrees  1.334244  0.05582975  0.8090375
   5             23    maxstat     1.127968  0.17075395  0.6432410
   5             25    maxstat     1.129190  0.17173014  0.6428472
   7             10    variance    1.313782  0.06226907  0.7895811
   7             15    variance    1.324030  0.06400505  0.7871634
   9             20    extratrees  1.296207  0.06965210  0.7838424
   9             26    extratrees  1.310

...

Random Forest 

78 samples
 6 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 63, 63, 62, 62, 62, 63, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1             10    maxstat     0.6367163  0.04910882  0.4070932
   1             12    extratrees  0.6966704  0.05059249  0.4080858
   2              2    extratrees  0.6640102  0.04179285  0.4201549
   2             15    extratrees  0.6978522  0.04896566  0.4098304
   5              6    variance    0.6856607  0.05057217  0.4068240
   5             14    maxstat     0.6401097  0.03662727  0.4058709
   7              6    extratrees  0.6875588  0.04196918  0.4169715
   7             10    variance    0.6815164  0.05017009  0.4041520
   9              7    variance    0.6800671  0.04432109  0.4074895
   9              8    maxstat     0.6362426  0.03825853  0.4120335
  10              6    extratrees  0.


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1917"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


#### Post-lockdown

In [92]:
bus_stops_r4_dir0_post

[1] "354"  "784"  "283"  "284"  "285"  "713"  "286"  "287"  "1351" "12"  
 [11] "1555" "1579" "1354" "1353" "17"   "742"  "805"  "806"  "807"  "1475"
 [21] "1474" "811"  "812"  "813"  "814"  "815"  "816"  "817"  "818"  "819" 
 [31] "820"  "821"  "822"  "823"  "824"  "825"  "826"  "827"  "828"  "829" 
 [41] "321"  "322"  "830"  "831"  "832"  "833"  "834"  "835"  "836"  "837" 
 [51] "838"  "839"  "840"  "841"  "842"  "843"  "844"  "845"  "846"  "848" 
 [61] "849"  "850"  "851"  "852"  "854"  "855"  "856"  "857"  "858"  "859" 
 [71] "860"  "861"  "1873" "1848" "1849" "1850" "867"  "868"  "869"  "870" 
 [81] "871"  "872"  "873"  "874"  "875"  "876"  "877"  "879"  "880"  "881" 
 [91] "882"  "883"  "884"  "885"  "886"  "887"  "888"  "889"  "890"  "891" 
[101] "1875" "894"  "1485" "897"  "898"  "1876" "892"  "505"  "18"   "19"  
[111] "1557" "1357" "21"   "22"   "23"   "24"   "25"   "900"  "901"  "902" 
[121] "903"  "1908" "905"  "1909" "907"  "908"  "1910" "1880" "1917" "1882"
[131] "1482" "1465" "1466" "1468" "1469" "1470" "1471" "1472" "1473" "1878"
[141] "1877" "1819"

In [ ]:
# 870

In [94]:
which(bus_stops_r4_dir0_post == '870', arr.ind = T)

[1] 80

In [95]:
for(i in bus_stops_r4_dir0_post[81:length(bus_stops_r4_dir0_post)]){
    print(i)
    RF_Ferns_and_Ranger('4', '0', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "871"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

145 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 116, 116, 116, 116, 116, 116, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9655172  0.9247094
   2     0.9827586  0.9559053
   3     0.9758621  0.9441843
   5     0.9862069  0.9648836
   6     0.9655172  0.9203681
   7     0.9862069  0.9640867
   9     0.9655172  0.9195384
  10     0.9793103  0.9469269
  11     0.9620690  0.9072237
  13     0.9448276  0.8680592
  14     0.9310345  0.8497996
  15     0.8965517  0.7691187

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 5.
Random Forest 

35 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 28, 29, 28, 28, 27, 28, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  split


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

244 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 195, 195, 195, 195, 196, 195, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     1.0000000  1.0000000
   2     0.9959184  0.9912343
   3     1.0000000  1.0000000
   5     0.9979592  0.9955576
   6     1.0000000  1.0000000
   7     1.0000000  1.0000000
   9     1.0000000  1.0000000
  10     0.9979592  0.9955576
  11     0.9959184  0.9911151
  13     0.9979592  0.9955576
  14     0.9918367  0.9825832
  15     0.9979592  0.9955576

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

84 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 67, 68, 67, 67, 67, 67, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  split

...

Random Ferns 

372 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 298, 298, 298, 297, 297, 298, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9665586  0.9098482
   2     0.9785946  0.9424335
   3     0.9813153  0.9484133
   5     0.9825946  0.9512655
   6     0.9905766  0.9725705
   7     0.9852973  0.9588581
   9     0.9785766  0.9392496
  10     0.9852252  0.9577632
  11     0.9759099  0.9320346
  13     0.9785766  0.9398113
  14     0.9718559  0.9200844
  15     0.9691712  0.9155353

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 6.
Random Forest 

76 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 61, 61, 61, 61, 60, 61, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  split


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

247 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 198, 198, 198, 196, 198, 198, ... 
Resampling results across tuning parameters:

  depth  Accuracy     Kappa
   1     0.003921569  0    
   2     0.003921569  0    
   3     0.003921569  0    
   5     0.003921569  0    
   6     0.003921569  0    
   7     0.003921569  0    
   9     0.003921569  0    
  10     0.003921569  0    
  11     0.003921569  0    
  13     0.003921569  0    
  14     0.003921569  0    
  15     0.003921569  0    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.


Warning message in confusionMatrix.default(y_clf_test, rf_random_pred):
“Levels are not in the same order for reference and data. Refactoring data to match.”


ERROR: Error in check_dims(x = x, y = y): nrow(x) > 1 is not TRUE


### Vanilla RF

In [81]:
for(i in bus_stops_r4_dir0_post){
    print(i)
    vanilla_rf('4', '0', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "354"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

107 samples
  6 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 86, 86, 86, 85, 85, 86, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE     
   1             10    maxstat     1.885248  0.10359408  1.362713
   1             12    extratrees  2.211979  0.04634940  1.644437
   2              2    extratrees  2.014555  0.05375990  1.462178
   2             15    extratrees  2.195630  0.04957996  1.629715
   5              6    variance    2.130894  0.05737864  1.574927
   5             14    maxstat     1.875554  0.11793918  1.350866
   7              6    extratrees  2.084788  0.05652763  1.537699
   7             10    variance    2.117648  0.06267245  1.559235
   9              7    variance    2.083258  0.06161118  1.539632
   9              8    maxstat     1.875800  0.11395388  1.355218
  10              6    extratrees  2.039704  0.05867130  


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "283"


...

[1] "Done!"
[1] "_/|_/|_"
[1] "1877"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1819"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


In [56]:
which(bus_stops_r4_dir0_post == '1876', arr.ind = T)

[1] 106

In [ ]:
# 354, 889, 1876, 870, 889, 1876, 1004

In [57]:
for(i in bus_stops_r4_dir0_post[107:length(bus_stops_r4_dir0_post)]){
    print(i)
    RF_Ferns_and_Ranger('4', '0', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "892"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "18"


...

[1] "Done!"
[1] "_/|_/|_"
[1] "1877"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_logical(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_logical(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1819"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


In [100]:
bus_stops_r4_dir1_pre

[1] "923"  "924"  "925"  "926"  "927"  "928"  "929"  "930"  "931"  "932" 
 [11] "933"  "934"  "935"  "936"  "1578" "939"  "941"  "1860" "943"  "1477"
 [21] "946"  "947"  "948"  "1883" "1919" "951"  "1889" "1853" "952"  "953" 
 [31] "954"  "955"  "956"  "957"  "959"  "960"  "961"  "962"  "963"  "964" 
 [41] "966"  "967"  "968"  "969"  "970"  "971"  "972"  "1545" "1911" "975" 
 [51] "976"  "977"  "978"  "979"  "980"  "1862" "981"  "982"  "983"  "984" 
 [61] "985"  "986"  "987"  "988"  "989"  "990"  "991"  "992"  "993"  "994" 
 [71] "995"  "407"  "408"  "409"  "412"  "413"  "996"  "997"  "998"  "1820"
 [81] "999"  "488"  "489"  "569"  "789"  "1351" "1885" "1003" "1004" "1910"
 [91] "1016" "1017" "1018" "1019" "1020" "1021" "1022" "1023" "1487" "138" 
[101] "139"  "140"  "141"  "142"  "143"  "771"  "144"  "145"  "163"  "164" 
[111] "165"  "1361" "1589" "12"   "1555" "1579" "1354" "1353" "17"   "742" 
[121] "805"  "806"  "807"  "1475" "505"  "690"  "1884" "1560" "166"  "167" 
[131] "169"  "170"  "171"  "172"  "1015"

In [101]:
for(i in bus_stops_r4_dir1_pre[1:length(bus_stops_r4_dir1_pre)]){
    print(i)
    RF_Ferns_and_Ranger('4', '1', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "923"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

2967 samples
   7 predictor
   2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 2374, 2374, 2373, 2374, 2373, 2374, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9639342  0.9130858
   2     0.9802783  0.9510684
   3     0.9912359  0.9757166
   5     0.9914017  0.9763078
   6     0.9836556  0.9564146
   7     0.9976411  0.9933307
   9     0.9924152  0.9787871
  10     0.9890428  0.9698094
  11     0.9900588  0.9723433
  13     0.9966307  0.9904546
  14     0.9888784  0.9688989
  15     0.9897173  0.9714159

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 7.
Random Forest 

2298 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1838, 1839, 1839, 1838, 1838, 1839, ... 
Resampling results across tuning parameters:

  m


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

707 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 566, 566, 566, 565, 565, 565, ... 
Resampling results across tuning parameters:

  depth  Accuracy  Kappa
   1     1         1    
   2     1         1    
   3     1         1    
   5     1         1    
   6     1         1    
   7     1         1    
   9     1         1    
  10     1         1    
  11     1         1    
  13     1         1    
  14     1         1    
  15     1         1    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

202 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 162, 162, 161, 161, 162, 163, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1             

...

[1] "Done!"
[1] "_/|_/|_"
[1] "172"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1015"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message in names(board_train) == c("service_kind", "hour"):
“longer object length is not a multiple of shorter object length”
Warning message in names(board_test) == c("service_kind", "hour"):
“longer object length is not a multiple of shorter object length”
Warning message:
“Unknown or uninitialised column: `board_count`.”
Warning message:
“Unknown or unini

[1] "Done!"
[1] "_/|_/|_"


In [103]:
which(bus_stops_r4_dir1_pre == '1004', arr.ind = T)

[1] 89

In [ ]:
# 1004

In [105]:
for(i in bus_stops_r4_dir1_pre[90:length(bus_stops_r4_dir1_pre)]){
    print(i)
    vanilla_rf('4', '1', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "1910"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

66 samples
 6 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 53, 53, 54, 52, 52, 53, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE     
   1              3    maxstat     1.668733  0.04049357  1.429707
   1             14    variance    1.802388  0.03105001  1.518939
   2              7    maxstat     1.683860  0.03865373  1.435444
   2              9    variance    1.798492  0.03519553  1.517370
   5              9    maxstat     1.689797  0.03504180  1.437163
   5             12    extratrees  1.798785  0.03460565  1.512947
   5             12    variance    1.799313  0.03523821  1.518143
   7              6    extratrees  1.791234  0.03862854  1.505443
   7             10    extratrees  1.797048  0.03366997  1.511995
   9              4    extratrees  1.773151  0.04034848  1.490949
   9             15    variance    1.793700  0.04093302  1.


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1017"


...

[1] "Done!"
[1] "_/|_/|_"
[1] "172"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1015"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message in names(board_train) == c("service_kind", "hour"):
“longer object length is not a multiple of shorter object length”
Warning message in names(board_test) == c("service_kind", "hour"):
“longer object length is not a multiple of shorter object length”
Warning message:
“Unknown or uninitialised column: `board_count`.”
Warning message:
“Unknown or unini

[1] "Done!"
[1] "_/|_/|_"


In [82]:
for(i in bus_stops_r4_dir1_post[1:length(bus_stops_r4_dir1_post)]){
    print(i)
    vanilla_rf('4', '1', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "1883"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

369 samples
  6 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 295, 296, 295, 295, 295, 297, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared     MAE     
   1             10    extratrees  3.373833  0.003964011  2.385906
   1             12    extratrees  3.384530  0.003808783  2.396213
   2             15    maxstat     2.899737  0.045784411  2.010268
   2             24    extratrees  3.387784  0.003833992  2.398695
   5             12    maxstat     2.899505  0.042251828  2.009607
   5             23    maxstat     2.902565  0.045982525  2.015153
   7             10    extratrees  3.289520  0.003271770  2.322938
   7             20    extratrees  3.309725  0.003501079  2.340850
   9              6    maxstat     2.895428  0.043406892  2.007288
   9             20    extratrees  3.285825  0.003296285  2.323768
  10             10    variance    3.280


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

500 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 400, 400, 400, 400, 400, 401, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE     
   1              6    extratrees  2.209263  0.01515908  1.724179
   1             25    maxstat     2.017750  0.07872766  1.566783
   2              8    maxstat     2.025343  0.06388399  1.577859
   2             12    extratrees  2.240749  0.01335313  1.747358
   5              6    maxstat     2.026837  0.06516381  1.582357
   5             12    extratrees  2.231851  0.01370545  1.740905
   5             25    extratrees  2.235952  0.01386381  1.740795
   7             10    variance    2.226665  0.01451138  1.732941
   7             15    extratrees  2.224226  0.01457169  1.732782
   9             20    extratrees  2.219941  0.01510812  1.728500
   9             25    variance    2.224844  0.0153

...

[1] "Done!"
[1] "_/|_/|_"
[1] "2198"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "808"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message:
“Unknown or uninitialised column: `board_count`.”


[1] "Done!"
[1] "_/|_/|_"


In [ ]:
# 283, 713, 286

In [111]:
which(bus_stops_r9_dir0_pre == '1087', arr.ind = T)

[1] 25

In [ ]:
# 285, 287, 1087

In [112]:
for(i in bus_stops_r9_dir0_pre[26:length(bus_stops_r9_dir0_pre)]){
    print(i)
    RF_Ferns_and_Ranger('9', '0', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "1088"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

344 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 276, 275, 275, 275, 275, 274, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9273000  0.6454373
   2     0.8998465  0.5835320
   3     0.8970722  0.5708391
   5     0.9287486  0.6470722
   6     0.9171331  0.6085414
   7     0.9127421  0.5980121
   9     0.9098228  0.5876343
  10     0.9012307  0.5637042
  11     0.9026391  0.5699501
  13     0.8924303  0.5421786
  14     0.8693862  0.4910166
  15     0.8807520  0.5113607

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 5.


Warning message in train.default(x, y, weights = w, ...):
“You are trying to do regression and your outcome only has two possible values Are you trying to do classification? If so, use a 2 level factor as your outcome column.”
Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

26 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 21, 21, 21, 20, 21, 21, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared   MAE      
   1             15    extratrees  0.3636102  0.3353588  0.2659084
   1             28    maxstat     0.3651241  0.3089931  0.2763125
   2             22    variance    0.3570058  0.3181069  0.2573872
   2             33    variance    0.3641895  0.3095165  0.2564155
   5              2    maxstat     0.3816217  0.3753582  0.3139703
   5             18    variance    0.3539271  0.3388379  0.2562443
   5             24    variance    0.3570998  0.3200773  0.2558056
   7             25    extratrees  0.3607086  0.3347127  0.2634664
   7             25    variance    0.3574906  0.3329945  0.2571441
   9              6    variance    0.3569020  0.3571188  0.2730510
   9             32    maxstat     0.3673012  0.

...

Random Ferns 

1053 samples
   7 predictor
   2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 842, 843, 843, 841, 843, 843, ... 
Resampling results across tuning parameters:

  depth  Accuracy     Kappa
   1     0.003796025  0    
   2     0.001891264  0    
   3     0.001891264  0    
   5     0.001891264  0    
   6     0.001891264  0    
   7     0.001891264  0    
   9     0.001891264  0    
  10     0.001891264  0    
  11     0.001891264  0    
  13     0.001891264  0    
  14     0.001891264  0    
  15     0.001891264  0    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.


Warning message in confusionMatrix.default(y_clf_test, rf_random_pred):
“Levels are not in the same order for reference and data. Refactoring data to match.”
Warning message in train.default(x, y, weights = w, ...):
“You are trying to do regression and your outcome only has two possible values Are you trying to do classification? If so, use a 2 level factor as your outcome column.”
Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

2 samples
7 predictors

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1, 1, 1, 1 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE  Rsquared  MAE
  1              10    maxstat     2     NaN       2  
  1              14    maxstat     2     NaN       2  
  1              15    extratrees  2     NaN       2  
  1              20    extratrees  2     NaN       2  
  1              20    maxstat     2     NaN       2  
  1              21    extratrees  2     NaN       2  
  1              23    extratrees  2     NaN       2  
  1              24    variance    2     NaN       2  
  1              25    extratrees  2     NaN       2  
  1              25    variance    2     NaN       2  
  1              28    maxstat     2     NaN       2  
  1              32    variance    2     NaN       2  
  1              33    extratrees  2     NaN       2  
  2               6    maxstat   


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

1311 samples
   7 predictor
   2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1050, 1049, 1048, 1048, 1049, 1050, ... 
Resampling results across tuning parameters:

  depth  Accuracy  Kappa
   1     1         1    
   2     1         1    
   3     1         1    
   5     1         1    
   6     1         1    
   7     1         1    
   9     1         1    
  10     1         1    
  11     1         1    
  13     1         1    
  14     1         1    
  15     1         1    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

518 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 414, 415, 414, 414, 415, 415, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared     MAE      
   1   

In [89]:
for(i in bus_stops_r9_dir0_pre[9:length(bus_stops_r9_dir0_pre)]){
    print(i)
    vanilla_rf('9', '0', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "287"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message in train.default(x, y, weights = w, ...):
“You are trying to do regression and your outcome only has two possible values Are you trying to do classification? If so, use a 2 level factor as your outcome column.”
Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = train

Random Forest 

129 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 103, 104, 103, 103, 103, 103, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared     MAE       
   1              6    extratrees  0.1548183  0.003158598  0.05907010
   1             25    variance    0.1549713  0.029347146  0.05293677
   2              6    extratrees  0.1523761  0.002973137  0.05789282
   2             12    maxstat     0.1347705  0.103813222  0.05220116
   5             20    extratrees  0.1488645  0.025630708  0.05501240
   5             23    maxstat     0.1351044  0.153138895  0.04848334
   5             25    maxstat     0.1354864  0.190398550  0.04828195
   7             10    variance    0.1457671  0.019092388  0.05675395
   7             15    variance    0.1434691  0.037661264  0.05386478
   9             20    extratrees  0.1444212  0.026879243  0.05696571
   9   


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

224 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 179, 180, 179, 179, 179, 178, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE      
   1              6    extratrees  1.727248  0.04569472  1.1521500
   1             25    variance    1.761480  0.05968840  1.1095311
   2              6    extratrees  1.719618  0.04606010  1.1503270
   2             12    maxstat     1.486622  0.17719283  0.9648673
   5             20    extratrees  1.717658  0.05677809  1.1204986
   5             23    maxstat     1.478207  0.18814166  0.9294392
   5             25    maxstat     1.475317  0.19127980  0.9251091
   7             10    variance    1.692770  0.06628100  1.1004258
   7             15    variance    1.705515  0.06710343  1.0908424
   9             20    extratrees  1.668286  0.07093675  1.0982370
   9             26    extratrees  1.668

...

Random Forest 

750 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 600, 601, 600, 600, 599, 600, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1             15    extratrees  1.0360616  0.01216200  0.6033189
   1             28    maxstat     0.8643804  0.13942994  0.4894886
   2             22    variance    1.0295163  0.01840574  0.5926334
   2             33    variance    1.0323764  0.01843709  0.5925385
   5              2    maxstat     0.9124384  0.11823323  0.6143445
   5             18    variance    1.0203913  0.01941539  0.5897472
   5             24    variance    1.0211821  0.02054473  0.5869705
   7             25    extratrees  1.0026250  0.02452462  0.5840094
   7             25    variance    1.0155557  0.02349543  0.5846801
   9              6    variance    0.9779462  0.02636858  0.5828972
   9             32    maxsta


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

1053 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 843, 843, 842, 842, 842, 842, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE        Rsquared      MAE        
   1             15    extratrees  0.07705857  0.1463171013  0.006221290
   1             28    maxstat     0.06678125  0.0001696706  0.006634824
   2             22    variance    0.07687890  0.1400015398  0.006234510
   2             33    variance    0.07712124  0.1558789697  0.006167730
   5              2    maxstat     0.05792250  0.0005601791  0.007496399
   5             18    variance    0.07586936  0.1536521227  0.006290676
   5             24    variance    0.07558250  0.1680203597  0.006210510
   7             25    extratrees  0.07340656  0.3898225988  0.005987528
   7             25    variance    0.07559650  0.1705245959  0.006254076
   9              6    variance    0.07482630


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

1311 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1050, 1049, 1048, 1049, 1048, 1049, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared     MAE      
   1             15    extratrees  1.0745174  0.004953344  0.7832638
   1             28    maxstat     0.9120793  0.087161981  0.6726065
   2             22    variance    1.0749316  0.005191454  0.7797034
   2             33    variance    1.0736013  0.005197029  0.7782091
   5              2    maxstat     0.9442831  0.071546862  0.7363276
   5             18    variance    1.0664246  0.005337475  0.7764399
   5             24    variance    1.0675310  0.005534188  0.7760586
   7             25    extratrees  1.0542031  0.006393673  0.7707111
   7             25    variance    1.0616575  0.005759064  0.7724403
   9              6    variance    1.0256319  0.007305292  0.7624095
   9      

In [91]:
bus_stops_r9_dir1_pre

[1] "1710" "1701" "1706" "1707" "1708" "1142" "1143" "1144" "1145" "1146"
[11] "1147" "1501" "1148" "1149" "1150" "1151" "1152" "1153" "1154" "1155"
[21] "1156" "1157" "1502" "1159" "1161" "1162" "1163" "1164" "1548" "1503"
[31] "1556" "1168" "1169" "1171" "1172" "1173" "1174" "1175" "1504" "1177"
[41] "1178" "1179" "1180" "1181" "1505" "1183" "1184" "1185" "1186" "1187"
[51] "1188" "1189" "1190" "1191" "1192" "1193" "1461" "142"  "143"  "771" 
[61] "144"  "145"  "1560" "163"  "164"  "165"  "1361" "1589" "166"  "167" 
[71] "169"  "170"  "171"  "172"  "505"  "690"

In [ ]:
# 690

In [92]:
for(i in bus_stops_r9_dir1_pre[1:length(bus_stops_r9_dir1_pre)]){
    print(i)
    vanilla_rf('9', '1', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "1710"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

1396 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1117, 1117, 1116, 1118, 1116, 1117, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE     
   1             15    extratrees  2.102016  0.01207948  1.648949
   1             28    maxstat     1.829983  0.08910527  1.403311
   2             22    variance    2.104041  0.01256291  1.651133
   2             33    variance    2.103451  0.01288516  1.649889
   5              2    maxstat     1.890338  0.08752431  1.418591
   5             18    variance    2.090152  0.01377694  1.637670
   5             24    variance    2.091139  0.01411685  1.639646
   7             25    extratrees  2.066533  0.01569357  1.616925
   7             25    variance    2.079534  0.01484204  1.629271
   9              6    variance    2.006419  0.02163132  1.563448
   9             32    maxstat     1.829149


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

1236 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 989, 989, 989, 988, 989, 989, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE     
   1             15    extratrees  1.516326  0.01189490  1.175087
   1             28    maxstat     1.303536  0.11407605  1.000799
   2             22    variance    1.515221  0.01362105  1.170963
   2             33    variance    1.514277  0.01401154  1.168806
   5              2    maxstat     1.367702  0.09800582  1.056075
   5             18    variance    1.503034  0.01505924  1.162806
   5             24    variance    1.504546  0.01497607  1.162813
   7             25    extratrees  1.487717  0.01749527  1.150854
   7             25    variance    1.498788  0.01640290  1.157919
   9              6    variance    1.446882  0.02254731  1.125963
   9             32    maxstat     1.302765  0.11

...

Random Forest 

177 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 142, 142, 142, 141, 141, 142, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE        Rsquared    MAE       
   1              6    extratrees  0.09670825  0.55986671  0.01952505
   1             25    maxstat     0.08180935  0.07316440  0.01805448
   2             12    extratrees  0.09874180  0.57770593  0.01881542
   2             25    maxstat     0.08123575  0.04877331  0.01812271
   5              6    extratrees  0.09003061  0.58995164  0.01921593
   5             23    maxstat     0.08146294  0.04347280  0.01858105
   5             26    extratrees  0.08956111  0.64246650  0.01748055
   7             10    variance    0.09039869  0.66924908  0.01954890
   7             15    extratrees  0.08952341  0.63231816  0.01796530
   9             12    variance    0.08842555  0.71725844  0.01921612
   9   


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

166 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 133, 133, 133, 132, 133, 132, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE      
   1              6    extratrees  2.031212  0.07170168  0.5997975
   1             25    variance    1.997592  0.13202001  0.5305967
   2              6    extratrees  2.017044  0.07007035  0.6051031
   2             12    maxstat     1.783800  0.14044094  0.5654438
   5             20    extratrees  1.947192  0.13641574  0.5433766
   5             23    maxstat     1.726323  0.21229999  0.4968690
   5             25    maxstat     1.720753  0.21690596  0.4922100
   7             10    variance    1.874048  0.15004626  0.5543136
   7             15    variance    1.844539  0.17583750  0.5159024
   9             20    extratrees  1.853687  0.18203486  0.5400147
   9             26    extratrees  1.852


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




ERROR: Error in cut.default(y, breaks, include.lowest = TRUE): invalid number of intervals


In [93]:
bus_stops_r9_dir0_post

[1] "354"  "505"  "784"  "283"  "284"  "285"  "713"  "286"  "287"  "1351"
[11] "12"   "1555" "1579" "1354" "1353" "17"   "742"  "19"   "1557" "1357"
[21] "1499" "1084" "1085" "1086" "1087" "1088" "1089" "1090" "1091" "1092"
[31] "1093" "1094" "1095" "1096" "1097" "1496" "1558" "1099" "1139" "1100"
[41] "1101" "1102" "1103" "1104" "1105" "1106" "1107" "1108" "1109" "1110"
[51] "1111" "1112" "1113" "1224" "1115" "1116" "1117" "1118" "1119" "1120"
[61] "1121" "1122" "1123" "1124" "1125" "1126" "1127" "1128" "1129" "1130"
[71] "1131" "1132" "1133" "1134" "1498" "1559" "1136" "1710"

In [ ]:
# 1122

In [95]:
which(bus_stops_r9_dir0_post == '1122', arr.ind = T)

[1] 62

In [96]:
for(i in bus_stops_r9_dir0_post[63:length(bus_stops_r9_dir0_post)]){
    print(i)
    vanilla_rf('9', '0', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "1123"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

92 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 74, 74, 74, 73, 73, 74, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared   MAE      
   1             10    extratrees  0.3826502  0.1117102  0.1837040
   1             12    extratrees  0.3840955  0.1154661  0.1845410
   2             15    extratrees  0.3801322  0.1324837  0.1837118
   2             19    variance    0.3683717  0.2463061  0.1593238
   5              6    maxstat     0.3251360  0.2948435  0.1685144
   5              7    variance    0.3548992  0.1697268  0.1711765
   7             10    extratrees  0.3501189  0.1813840  0.1769828
   7             20    maxstat     0.3058563  0.3817246  0.1318412
   9              8    extratrees  0.3457671  0.1845025  0.1769766
   9             20    extratrees  0.3468768  0.1843677  0.1755946
  10             10    extratrees  0.3443023  0.


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

119 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 95, 96, 95, 95, 95, 95, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1             10    extratrees  0.7627807  0.02925692  0.4600364
   1             12    extratrees  0.7665541  0.03048385  0.4610161
   2             15    maxstat     0.6236046  0.14425454  0.3618773
   2             24    extratrees  0.7695697  0.02770019  0.4559221
   5             12    maxstat     0.6217260  0.14348472  0.3689127
   5             23    maxstat     0.6275190  0.15675173  0.3458757
   7             10    extratrees  0.7173974  0.03811206  0.4420129
   7             20    extratrees  0.7384173  0.03627112  0.4455051
   9              6    maxstat     0.6285461  0.12562394  0.4007525
   9             20    extratrees  0.7237703  0.04107241  0.4390266
  10             10    variance    

...

Random Forest 

121 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 97, 97, 97, 96, 97, 97, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE       
   1             10    variance    0.2579485  0.05142427  0.09989277
   1             12    maxstat     0.2247630  0.13346108  0.09456781
   2              6    maxstat     0.2223511  0.10674589  0.10063349
   2             15    maxstat     0.2263641  0.14190028  0.09300364
   5             12    maxstat     0.2246160  0.13746709  0.09508854
   5             23    extratrees  0.2510910  0.07425872  0.09812754
   5             23    maxstat     0.2303185  0.15997194  0.08969778
   7             10    extratrees  0.2406678  0.06586350  0.10000894
   7             20    extratrees  0.2433132  0.08404234  0.09824788
   9              6    extratrees  0.2318547  0.08896775  0.09965611
   9             20    v


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

168 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 135, 135, 134, 134, 134, 134, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1             10    extratrees  0.9918598  0.09384381  0.6340635
   1             12    extratrees  0.9948348  0.09326040  0.6334237
   2             15    maxstat     0.8730244  0.16154945  0.5602949
   2             24    extratrees  0.9947529  0.09613912  0.6269699
   5             12    maxstat     0.8710132  0.15940887  0.5687780
   5             23    maxstat     0.8768753  0.16425825  0.5474301
   7             10    extratrees  0.9520555  0.10600205  0.6194352
   7             20    extratrees  0.9674328  0.10282736  0.6176518
   9              6    maxstat     0.8754838  0.15867497  0.6043200
   9             20    extratrees  0.9595266  0.10626383  0.6145028
  10             10    varian


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




ERROR: Error in cut.default(y, breaks, include.lowest = TRUE): invalid number of intervals


In [99]:
for(i in bus_stops_r9_dir1_post[1:length(bus_stops_r9_dir1_post)]){
    print(i)
    vanilla_rf('9', '1', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "1710"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

244 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 194, 197, 195, 195, 195, 196, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared     MAE     
   1             10    extratrees  2.355108  0.006138048  1.848183
   1             12    extratrees  2.368303  0.006645729  1.855480
   2             15    maxstat     1.957603  0.056936841  1.530670
   2             24    extratrees  2.362375  0.005890024  1.849882
   5             12    maxstat     1.957322  0.056594921  1.530864
   5             23    maxstat     1.960182  0.059628265  1.530199
   7             10    extratrees  2.247176  0.004944612  1.762221
   7             20    extratrees  2.279692  0.004660394  1.784896
   9              6    maxstat     1.952094  0.057003822  1.525364
   9             20    extratrees  2.244950  0.004570237  1.762058
  10             10    variance    2.246


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Forest 

268 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 214, 216, 214, 214, 214, 214, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared     MAE     
   1             10    extratrees  1.597191  0.009709467  1.231661
   1             12    extratrees  1.596265  0.010376288  1.229221
   2             15    maxstat     1.400826  0.072607203  1.086388
   2             24    extratrees  1.595508  0.010218523  1.227228
   5             12    maxstat     1.397172  0.072811900  1.086917
   5             23    maxstat     1.396198  0.079543633  1.077148
   7             10    extratrees  1.543676  0.014096533  1.191994
   7             20    extratrees  1.557890  0.013221233  1.197150
   9              6    maxstat     1.400112  0.066024119  1.094743
   9             20    extratrees  1.543576  0.015028079  1.188406
  10             10    variance    1.556

...

[1] "Done!"
[1] "_/|_/|_"
[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "690"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




ERROR: Error in cut.default(y, breaks, include.lowest = TRUE): invalid number of intervals


### Direction 1

#### Pre-lockdown

In [78]:
bus_stops_r4_dir0_pre = Pre_lock %>%  
    filter(route_id == '4', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r4_dir0_pre = unique(bus_stops_r4_dir1_pre)
bus_stops_r4_dir0_pre

[1] "923"  "924"  "925"  "926"  "927"  "928"  "929"  "930"  "931"  "932" 
 [11] "933"  "934"  "935"  "936"  "1578" "939"  "941"  "1860" "943"  "1477"
 [21] "946"  "947"  "948"  "1883" "1919" "951"  "1889" "1853" "952"  "953" 
 [31] "954"  "955"  "956"  "957"  "959"  "960"  "961"  "962"  "963"  "964" 
 [41] "966"  "967"  "968"  "969"  "970"  "971"  "972"  "1545" "1911" "975" 
 [51] "976"  "977"  "978"  "979"  "980"  "1862" "981"  "982"  "983"  "984" 
 [61] "985"  "986"  "987"  "988"  "989"  "990"  "991"  "992"  "993"  "994" 
 [71] "995"  "407"  "408"  "409"  "412"  "413"  "996"  "997"  "998"  "1820"
 [81] "999"  "488"  "489"  "569"  "789"  "1351" "1885" "1003" "1004" "1910"
 [91] "1016" "1017" "1018" "1019" "1020" "1021" "1022" "1023" "1487" "138" 
[101] "139"  "140"  "141"  "142"  "143"  "771"  "144"  "145"  "163"  "164" 
[111] "165"  "1361" "1589" "12"   "1555" "1579" "1354" "1353" "17"   "742" 
[121] "805"  "806"  "807"  "1475" "505"  "690"  "1884" "1560" "166"  "167" 
[131] "169"  "170"  "171"  "172"  "1015"

In [ ]:
#

In [78]:
which(bus_stops_r4_dir1_pre == '1876', arr.ind = T)

integer(0)

In [20]:
for(i in bus_stops_r4_dir1_pre[107:length(bus_stops_r4_dir1_pre)]){
    print(i)
    RF_Ferns_and_Ranger('4', '1', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "892"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "18"


...

[1] "Done!"
[1] "_/|_/|_"
[1] "1877"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_logical(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_logical(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1819"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


#### Post-lockdown

In [25]:
bus_stops_r4_dir1_post = Post_lock %>%  
    filter(route_id == '4', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r4_dir1_post = unique(bus_stops_r4_dir1_post)
bus_stops_r4_dir1_post

[1] "1883" "923"  "924"  "925"  "926"  "927"  "928"  "929"  "930"  "931" 
 [11] "932"  "933"  "934"  "935"  "936"  "1578" "939"  "941"  "1860" "943" 
 [21] "1477" "946"  "947"  "948"  "1919" "1820" "951"  "1889" "1853" "952" 
 [31] "953"  "954"  "955"  "956"  "957"  "959"  "960"  "961"  "962"  "963" 
 [41] "964"  "966"  "967"  "968"  "969"  "970"  "971"  "972"  "1545" "1911"
 [51] "975"  "976"  "977"  "978"  "979"  "980"  "1862" "981"  "982"  "983" 
 [61] "984"  "985"  "986"  "987"  "988"  "989"  "990"  "991"  "992"  "993" 
 [71] "994"  "995"  "407"  "408"  "409"  "412"  "413"  "996"  "997"  "998" 
 [81] "999"  "488"  "489"  "569"  "789"  "1351" "1885" "1003" "1004" "1015"
 [91] "1910" "12"   "1555" "1579" "1354" "1353" "17"   "1016" "742"  "1017"
[101] "805"  "1018" "806"  "1019" "1475" "1020" "1021" "1022" "1023" "505" 
[111] "690"  "1487" "138"  "139"  "140"  "141"  "142"  "143"  "771"  "144" 
[121] "145"  "163"  "164"  "165"  "1361" "1589" "1884" "1560" "166"  "167" 
[131] "169"  "170"  "171"  "172"  "807"  "1878" "2148" "2197" "2245" "2223"
[141] "1976" "1975" "2063" "2068" "2076" "1922" "2010" "568"  "2198" "808"

In [30]:
which(bus_stops_r4_dir1_post == '996', arr.ind = T)

[1] 78

In [ ]:
# 1883, 412

In [31]:
for(i in bus_stops_r4_dir1_post[79:length(bus_stops_r4_dir1_post)]){
    print(i)
    RF_Ferns_and_Ranger('4', '1', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "997"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

180 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 163, 161, 162, 162, 162, 163, ... 
Resampling results across tuning parameters:

  depth  Accuracy    Kappa       
   1     0.17107556  0.0015530861
   2     0.13423346  0.0011201857
   3     0.10272904  0.0006380286
   5     0.02535260  0.0000000000
   6     0.01968811  0.0000000000
   7     0.01598441  0.0000000000
   9     0.01598441  0.0000000000
  10     0.01598441  0.0000000000
  11     0.01598441  0.0000000000
  13     0.01598441  0.0000000000
  14     0.01598441  0.0000000000
  15     0.01598441  0.0000000000

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.


Warning message in confusionMatrix.default(y_clf_test, rf_random_pred):
“Levels are not in the same order for reference and data. Refactoring data to match.”
Warning message in train.default(x, y, weights = w, ...):
“You are trying to do regression and your outcome only has two possible values Are you trying to do classification? If so, use a 2 level factor as your outcome column.”
Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

3 samples
7 predictors

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 2, 2, 2, 2, 2, 2, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared  MAE      
  1               1    extratrees  0.6506667  NaN       0.6506667
  1               5    variance    0.6098889  NaN       0.6098889
  1               6    extratrees  0.6067778  NaN       0.6067778
  1              12    maxstat     0.6688889  NaN       0.6688889
  1              15    extratrees  0.6064444  NaN       0.6064444
  1              25    extratrees  0.6135556  NaN       0.6135556
  2               2    extratrees  0.6668889  NaN       0.6668889
  2               3    extratrees  0.6612222  NaN       0.6612222
  2               5    maxstat     0.6682222  NaN       0.6682222
  2               6    variance    0.6687778  NaN       0.6687778
  2               9    maxstat     0.6665556  NaN       0.6665556

...

[1] "Done!"
[1] "_/|_/|_"
[1] "807"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_logical(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_logical(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1878"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_logical(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_logical(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




ERROR: Error in na.fail.default(structure(list(y_clf_train = structure(c(2L, : missing values in object


## Route 1

### Pre-lockdown

In [36]:
bus_stops_r1_dir0_pre = Pre_lock %>%  
    filter(route_id == '1', direction_id == '0') %>%
    pull(stop_id)

bus_stops_r1_dir1_pre = Pre_lock %>%  
    filter(route_id == '1', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r1_dir0_pre = unique(bus_stops_r1_dir0_pre)
bus_stops_r1_dir1_pre = unique(bus_stops_r1_dir1_pre)

In [68]:
bus_stops_r1_dir0_pre

[1] "1351" "12"   "1555" "1579" "1354" "1353" "17"   "742"  "18"   "19"  
[11] "1557" "1357" "21"   "22"   "23"   "24"   "25"   "26"   "27"   "28"  
[21] "354"  "505"  "784"  "283"  "284"  "285"  "713"  "286"  "287"  "95"  
[31] "44"

In [71]:
which(bus_stops_r1_dir0_pre == '354', arr.ind = T)

[1] 21

#### Direction 0

In [ ]:
# c(354)

In [72]:
for(i in bus_stops_r1_dir0_pre[22:length(bus_stops_r1_dir0_pre)]){
    print(i)
    RF_Ferns_and_Ranger('1', '0', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

218 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 197, 195, 197, 196, 196, 197, ... 
Resampling results across tuning parameters:

  depth  Accuracy  Kappa
   1     1         1    
   2     1         1    
   3     1         1    
   5     1         1    
   6     1         1    
   7     1         1    
   9     1         1    
  10     1         1    
  11     1         1    
  13     1         1    
  14     1         1    
  15     1         1    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

92 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 83, 83, 83, 82, 83, 83, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared   MAE      
   1              6    e


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

142 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 128, 128, 128, 127, 127, 129, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9042369  0.7118119
   2     0.8996337  0.7060606
   3     0.8899267  0.6874717
   5     0.8924908  0.6952177
   6     0.8902686  0.6879472
   7     0.8832845  0.6785173
   9     0.8807204  0.6711451
  10     0.8665690  0.6272891
  11     0.8572283  0.6204330
  13     0.8500366  0.5917537
  14     0.8476557  0.5934600
  15     0.8430525  0.5812805

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

18 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 17, 16, 16, 16, 16, 16, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared  MAE      
   1              6    extratrees  0.7206130    1       0.6518169
   1             12    maxstat     0.6899688    1       0.6088818
   2              8    extratrees  0.7107929    1       0.6388778
   2             15    extratrees  0.6808124    1       0.6023793
   5              6    maxstat     0.7138144    1       0.6411682
   5             12    extratrees  0.6947548    1       0.6194548
   5             25    maxstat     0.6664869    1       0.5850420
   7             15    variance    0.6547210    1       0.5671762
   7             25    variance    0.6598004    1       0.5676312
   9             20    extratrees  0.6897207    1       0.6129497
   9             25    extratrees  0.6827770    1       0.


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_logical(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_logical(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




ERROR: Error in na.fail.default(structure(list(y_clf_train = structure(c(1L, : missing values in object


#### Direction 1

In [30]:
for(i in bus_stops_r1_dir1_pre[1:length(bus_stops_r1_dir1_pre)]){
    print(i)
    RF_Ferns_and_Ranger('1', '1', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "95"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

1474 samples
   7 predictor
   2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 1327, 1327, 1327, 1326, 1326, 1328, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9997748  0.9994711
   2     1.0000000  1.0000000
   3     1.0000000  1.0000000
   5     1.0000000  1.0000000
   6     1.0000000  1.0000000
   7     1.0000000  1.0000000
   9     1.0000000  1.0000000
  10     1.0000000  1.0000000
  11     1.0000000  1.0000000
  13     1.0000000  1.0000000
  14     1.0000000  1.0000000
  15     1.0000000  1.0000000

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 2.
Random Forest 

1029 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 926, 926, 925, 926, 927, 927, ... 
Resampling results across tuning parameters:

  min.n


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

776 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 699, 698, 698, 698, 698, 699, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9991342  0.9980658
   2     1.0000000  1.0000000
   3     1.0000000  1.0000000
   5     1.0000000  1.0000000
   6     1.0000000  1.0000000
   7     1.0000000  1.0000000
   9     1.0000000  1.0000000
  10     1.0000000  1.0000000
  11     1.0000000  1.0000000
  13     1.0000000  1.0000000
  14     1.0000000  1.0000000
  15     1.0000000  1.0000000

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 2.
Random Forest 

258 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 232, 233, 233, 232, 232, 233, ... 
Resampling results across tuning parameters:

  min.node.size  m

...

Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

21 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 19, 19, 19, 18, 19, 19, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared  MAE      
   1             15    extratrees  0.9522678    1       0.7654337
   1             20    maxstat     0.8859779    1       0.7429910
   2             18    variance    0.9490518    1       0.7704611
   2             33    extratrees  0.9671462    1       0.7729462
   5              2    maxstat     0.7682337    1       0.6666921
   5              6    variance    0.8708716    1       0.7216944
   5             14    extratrees  0.8747562    1       0.7108981
   7              6    maxstat     0.8010418    1       0.6867969
   7             25    extratrees  0.9067866    1       0.7330813
   9             24    variance    0.9597278    1       0.7846830
   9             25    variance    0.9636202    1       0.


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

404 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 364, 364, 364, 363, 363, 364, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.8094309  0.3298943
   2     0.7946138  0.2837877
   3     0.7887805  0.2776372
   5     0.7905081  0.2826427
   6     0.7846951  0.2694858
   7     0.7896138  0.2773317
   9     0.7797561  0.2624780
  10     0.7797561  0.2657913
  11     0.7739837  0.2557372
  13     0.7657520  0.2481163
  14     0.7656911  0.2456964
  15     0.7607114  0.2425366

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.


ERROR: Error in cut.default(y, breaks, include.lowest = TRUE): invalid number of intervals


### Direction 1

In [65]:
bus_stops_r1_dir0_post = Post_lock %>%  
    filter(route_id == '1', direction_id == '0') %>%
    pull(stop_id)

bus_stops_r1_dir0_post = unique(bus_stops_r1_dir0_post)

In [66]:
bus_stops_r1_dir0_post

[1] "354"  "505"  "784"  "283"  "284"  "285"  "713"  "286"  "287"  "1351"
[11] "12"   "1555" "1579" "1354" "1353" "17"   "742"  "18"   "19"   "1557"
[21] "1357" "21"   "22"   "23"   "24"   "25"   "26"   "27"   "28"   "95"

In [ ]:
which(bus_stops_r1_dir1_post =='1582', arr.ind =T)

In [67]:
for(i in bus_stops_r1_dir0_post[1:length(bus_stops_r1_dir0_post)]){
    print(i)
    RF_Ferns_and_Ranger('1', '0', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "354"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_logical(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_logical(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "784"


...

Random Forest 

44 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 40, 40, 40, 39, 40, 40, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared   MAE      
   1              6    extratrees  1.2755764  0.2914200  0.9552655
   1             25    maxstat     1.0600227  0.2525398  0.8349657
   2             12    extratrees  1.2907386  0.2893079  0.9632333
   2             25    maxstat     1.0562690  0.2299936  0.8307821
   5              6    extratrees  1.1968516  0.2691632  0.9138224
   5             23    maxstat     1.0526162  0.2354865  0.8304674
   5             26    extratrees  1.2782730  0.2937105  0.9564901
   7             10    variance    1.1991444  0.2326625  0.8987667
   7             15    extratrees  1.2223159  0.2561052  0.9217374
   9             12    variance    1.1928293  0.2245345  0.8968979
   9             20    extratrees  1.2269496  0


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

154 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 139, 138, 138, 139, 138, 139, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9890079  0.9739419
   2     0.9869246  0.9720486
   3     0.9867857  0.9696326
   5     0.9786111  0.9532681
   6     0.9760913  0.9481105
   7     0.9784524  0.9520732
   9     0.9719246  0.9387033
  10     0.9717857  0.9369070
  11     0.9717857  0.9389720
  13     0.9674802  0.9296124
  14     0.9655357  0.9256311
  15     0.9631746  0.9188419

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

47 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 43, 42, 42, 42, 43, 42, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  spl


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


### Direction 1

In [49]:
bus_stops_r1_dir1_post = Post_lock %>%  
    filter(route_id == '1', direction_id == '1') %>%
    pull(stop_id)

bus_stops_r1_dir1_post = unique(bus_stops_r1_dir1_post)

In [50]:
bus_stops_r1_dir1_post

[1] "95"   "1891" "1915" "72"   "1892" "161"  "74"   "75"   "158"  "155" 
[11] "146"  "81"   "90"   "1486" "1899" "148"  "1731" "1797" "150"  "151" 
[21] "152"  "103"  "104"  "105"  "107"  "108"  "109"  "110"  "111"  "112" 
[31] "113"  "114"  "115"  "116"  "1912" "118"  "1914" "1358" "1582" "124" 
[41] "125"  "126"  "127"  "128"  "129"  "130"  "132"  "133"  "134"  "136" 
[51] "137"  "1487" "138"  "139"  "140"  "141"  "142"  "143"  "771"  "144" 
[61] "145"  "157"  "1913" "100"  "101"  "106"  "1488" "1684" "1560" "163" 
[71] "164"  "165"  "1361" "1589" "166"  "167"  "169"  "170"  "171"  "172" 
[81] "505"  "102"  "690"

In [ ]:
# 95, 72, 1892, 1582, 126, 127, 140

In [ ]:
which(bus_stops_r1_dir1_post =='144', arr.ind =T)

In [64]:
for(i in bus_stops_r1_dir1_post[61:length(bus_stops_r1_dir1_post)]){
    print(i)
    RF_Ferns_and_Ranger('1', '1', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "145"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

231 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 208, 208, 209, 207, 208, 208, ... 
Resampling results across tuning parameters:

  depth  Accuracy    Kappa       
   1     0.34649758  0.0015684464
   2     0.36522288  0.0169380033
   3     0.31718819  0.0009750065
   5     0.23489789  0.0060502590
   6     0.19989570  0.0055960756
   7     0.13216952  0.0021181375
   9     0.07744291  0.0021173187
  10     0.04868797  0.0009613461
  11     0.04458169  0.0004131425
  13     0.02566974  0.0000000000
  14     0.02270531  0.0000000000
  15     0.02125604  0.0000000000

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 2.


Warning message in confusionMatrix.default(y_clf_test, rf_random_pred):
“Levels are not in the same order for reference and data. Refactoring data to match.”
Warning message in train.default(x, y, weights = w, ...):
“You are trying to do regression and your outcome only has two possible values Are you trying to do classification? If so, use a 2 level factor as your outcome column.”
Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

5 samples
7 predictors

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 4, 4, 4, 4, 4, 4, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared  MAE      
  1               6    extratrees  0.6661889  NaN       0.6661889
  1              10    variance    0.6163222  NaN       0.6163222
  1              12    variance    0.6023111  NaN       0.6023111
  1              20    extratrees  0.6438667  NaN       0.6438667
  1              25    maxstat     0.6777000  NaN       0.6777000
  2               1    maxstat     0.6085000  NaN       0.6085000
  2               6    variance    0.6342444  NaN       0.6342444
  2              15    extratrees  0.6505000  NaN       0.6505000
  2              25    maxstat     0.6826333  NaN       0.6826333
  3               3    extratrees  0.6416889  NaN       0.6416889
  3              15    extratrees  0.6368000  NaN       0.6368000

...

Random Ferns 

112 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 101, 101, 101, 100, 101, 101, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9095960  0.7738531
   2     0.9159091  0.7910945
   3     0.8916667  0.7324345
   5     0.8949495  0.7348657
   6     0.8919192  0.7302341
   7     0.8861111  0.7181422
   9     0.8861111  0.7181422
  10     0.8800505  0.7073710
  11     0.8858586  0.7218439
  13     0.8712121  0.6867586
  14     0.8742424  0.6928982
  15     0.8742424  0.6954193

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 2.


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

20 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (10 fold, repeated 3 times) 
Summary of sample sizes: 18, 18, 18, 18, 18, 18, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared  MAE      
   1              6    extratrees  1.0072248    1       0.9250679
   1             25    maxstat     0.9033589    1       0.8369612
   2             12    extratrees  1.0282315    1       0.9304863
   2             25    maxstat     0.9023615    1       0.8356197
   5              6    extratrees  0.9605774    1       0.8855984
   5             23    maxstat     0.8980863    1       0.8315345
   5             26    extratrees  1.0285767    1       0.9213417
   7             10    variance    0.9838219    1       0.8980603
   7             15    extratrees  0.9892968    1       0.9006435
   9             12    variance    0.9724626    1       0.8897169
   9             20    extratrees  0.9621307    1       0.


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


## Route 4 

### Direction 0

#### Pre-lockdown

In [97]:
bus_stops_r4_dir0_pre

[1] "354"  "505"  "284"  "285"  "713"  "286"  "287"  "1351" "12"   "1555"
 [11] "1579" "1354" "1353" "17"   "742"  "805"  "806"  "807"  "1475" "1474"
 [21] "811"  "812"  "813"  "814"  "815"  "816"  "817"  "818"  "819"  "820" 
 [31] "821"  "822"  "823"  "824"  "825"  "826"  "827"  "828"  "829"  "321" 
 [41] "322"  "830"  "831"  "832"  "833"  "834"  "835"  "836"  "837"  "838" 
 [51] "839"  "840"  "841"  "842"  "843"  "844"  "845"  "846"  "848"  "849" 
 [61] "850"  "851"  "852"  "854"  "892"  "855"  "1875" "856"  "894"  "784" 
 [71] "857"  "858"  "283"  "859"  "897"  "860"  "861"  "898"  "1873" "1848"
 [81] "1849" "1850" "1819" "867"  "1877" "868"  "869"  "870"  "871"  "872" 
 [91] "873"  "874"  "875"  "876"  "877"  "879"  "880"  "881"  "882"  "883" 
[101] "884"  "885"  "886"  "887"  "888"  "889"  "890"  "891"  "1485" "1876"
[111] "1482" "1465" "1466" "1468" "1469" "1470" "1471" "1472" "1473" "1878"
[121] "18"   "19"   "1557" "1357" "21"   "22"   "23"   "24"   "25"   "900" 
[131] "901"  "902"  "903"  "1908" "905"  "1909" "907"  "908"  "1910" "1880"
[141] "1917" "1882"

In [ ]:
# 713, 286

In [101]:
which(bus_stops_r4_dir0_pre == '713', arr.ind = T)

[1] 5

In [103]:
for(i in bus_stops_r4_dir0_pre[7:length(bus_stops_r4_dir0_pre)]){
    print(i)
    RF_Ferns_and_Ranger('4', '0', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "287"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

405 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 324, 324, 325, 323, 324, 324, ... 
Resampling results across tuning parameters:

  depth  Accuracy  Kappa
   1     1         1    
   2     1         1    
   3     1         1    
   5     1         1    
   6     1         1    
   7     1         1    
   9     1         1    
  10     1         1    
  11     1         1    
  13     1         1    
  14     1         1    
  15     1         1    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

174 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 139, 140, 139, 139, 139, 139, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE      
   1              


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

1696 samples
   7 predictor
   2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1357, 1357, 1357, 1357, 1356, 1356, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9737854  0.9257457
   2     0.9728594  0.9243197
   3     0.9820206  0.9467577
   5     0.9766987  0.9332737
   6     0.9749601  0.9266361
   7     0.9690438  0.9103694
   9     0.9820189  0.9463133
  10     0.9649158  0.9004891
  11     0.9778908  0.9346664
  13     0.9731823  0.9213186
  14     0.9693441  0.9108594
  15     0.9678604  0.9070249

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 3.
Random Forest 

1354 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1083, 1083, 1084, 1083, 1083, 1082, ... 
Resampling results across tuning parameters:

  m

...

[1] "Done!"
[1] "_/|_/|_"
[1] "1917"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1882"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


#### Post-lockdown

In [104]:
bus_stops_r4_dir0_post

[1] "354"  "784"  "283"  "284"  "285"  "713"  "286"  "287"  "1351" "12"  
 [11] "1555" "1579" "1354" "1353" "17"   "742"  "805"  "806"  "807"  "1475"
 [21] "1474" "811"  "812"  "813"  "814"  "815"  "816"  "817"  "818"  "819" 
 [31] "820"  "821"  "822"  "823"  "824"  "825"  "826"  "827"  "828"  "829" 
 [41] "321"  "322"  "830"  "831"  "832"  "833"  "834"  "835"  "836"  "837" 
 [51] "838"  "839"  "840"  "841"  "842"  "843"  "844"  "845"  "846"  "848" 
 [61] "849"  "850"  "851"  "852"  "854"  "855"  "856"  "857"  "858"  "859" 
 [71] "860"  "861"  "1873" "1848" "1849" "1850" "867"  "868"  "869"  "870" 
 [81] "871"  "872"  "873"  "874"  "875"  "876"  "877"  "879"  "880"  "881" 
 [91] "882"  "883"  "884"  "885"  "886"  "887"  "888"  "889"  "890"  "891" 
[101] "1875" "894"  "1485" "897"  "898"  "1876" "892"  "505"  "18"   "19"  
[111] "1557" "1357" "21"   "22"   "23"   "24"   "25"   "900"  "901"  "902" 
[121] "903"  "1908" "905"  "1909" "907"  "908"  "1910" "1880" "1917" "1882"
[131] "1482" "1465" "1466" "1468" "1469" "1470" "1471" "1472" "1473" "1878"
[141] "1877" "1819"

In [ ]:
# 870, 1876

In [108]:
which(bus_stops_r4_dir0_post == '1876', arr.ind = T)

[1] 106

In [109]:
for(i in bus_stops_r4_dir0_post[107:length(bus_stops_r4_dir0_post)]){
    print(i)
    RF_Ferns_and_Ranger('4', '0', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "892"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "18"


...

[1] "Done!"
[1] "_/|_/|_"
[1] "1877"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1819"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


## Route 4 

### Direction 1

#### Pre-lockdown

In [97]:
bus_stops_r4_dir1_pre

[1] "923"  "924"  "925"  "926"  "927"  "928"  "929"  "930"  "931"  "932" 
 [11] "933"  "934"  "935"  "936"  "1578" "939"  "941"  "1860" "943"  "1477"
 [21] "946"  "947"  "948"  "1883" "1919" "951"  "1889" "1853" "952"  "953" 
 [31] "954"  "955"  "956"  "957"  "959"  "960"  "961"  "962"  "963"  "964" 
 [41] "966"  "967"  "968"  "969"  "970"  "971"  "972"  "1545" "1911" "975" 
 [51] "976"  "977"  "978"  "979"  "980"  "1862" "981"  "982"  "983"  "984" 
 [61] "985"  "986"  "987"  "988"  "989"  "990"  "991"  "992"  "993"  "994" 
 [71] "995"  "407"  "408"  "409"  "412"  "413"  "996"  "997"  "998"  "1820"
 [81] "999"  "488"  "489"  "569"  "789"  "1351" "1885" "1003" "1004" "1910"
 [91] "1016" "1017" "1018" "1019" "1020" "1021" "1022" "1023" "1487" "138" 
[101] "139"  "140"  "141"  "142"  "143"  "771"  "144"  "145"  "163"  "164" 
[111] "165"  "1361" "1589" "12"   "1555" "1579" "1354" "1353" "17"   "742" 
[121] "805"  "806"  "807"  "1475" "505"  "690"  "1884" "1560" "166"  "167" 
[131] "169"  "170"  "171"  "172"  "1015"

In [ ]:
#

In [ ]:
which()

In [111]:
for(i in bus_stops_r4_dir1_pre[1:length(bus_stops_r4_dir1_pre)]){
    print(i)
    RF_Ferns_and_Ranger('4', '1', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "923"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

2967 samples
   7 predictor
   2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 2374, 2374, 2373, 2374, 2373, 2374, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9639342  0.9130858
   2     0.9802783  0.9510684
   3     0.9912359  0.9757166
   5     0.9914017  0.9763078
   6     0.9836556  0.9564146
   7     0.9976411  0.9933307
   9     0.9924152  0.9787871
  10     0.9890428  0.9698094
  11     0.9900588  0.9723433
  13     0.9966307  0.9904546
  14     0.9888784  0.9688989
  15     0.9897173  0.9714159

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 7.
Random Forest 

2298 samples
   7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1838, 1839, 1839, 1838, 1838, 1839, ... 
Resampling results across tuning parameters:

  m


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

707 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 566, 566, 566, 565, 565, 565, ... 
Resampling results across tuning parameters:

  depth  Accuracy  Kappa
   1     1         1    
   2     1         1    
   3     1         1    
   5     1         1    
   6     1         1    
   7     1         1    
   9     1         1    
  10     1         1    
  11     1         1    
  13     1         1    
  14     1         1    
  15     1         1    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

202 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 162, 162, 161, 161, 162, 163, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared    MAE      
   1             

...

[1] "Done!"
[1] "_/|_/|_"
[1] "172"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1015"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message in names(board_train) == c("service_kind", "hour"):
“longer object length is not a multiple of shorter object length”
Warning message in names(board_test) == c("service_kind", "hour"):
“longer object length is not a multiple of shorter object length”
Warning message:
“Unknown or uninitialised column: `board_count`.”
Warning message:
“Unknown or unini

[1] "Done!"
[1] "_/|_/|_"


In [ ]:
#### Post-lockdown

In [112]:
bus_stops_r4_dir1_post

[1] "1883" "923"  "924"  "925"  "926"  "927"  "928"  "929"  "930"  "931" 
 [11] "932"  "933"  "934"  "935"  "936"  "1578" "939"  "941"  "1860" "943" 
 [21] "1477" "946"  "947"  "948"  "1919" "1820" "951"  "1889" "1853" "952" 
 [31] "953"  "954"  "955"  "956"  "957"  "959"  "960"  "961"  "962"  "963" 
 [41] "964"  "966"  "967"  "968"  "969"  "970"  "971"  "972"  "1545" "1911"
 [51] "975"  "976"  "977"  "978"  "979"  "980"  "1862" "981"  "982"  "983" 
 [61] "984"  "985"  "986"  "987"  "988"  "989"  "990"  "991"  "992"  "993" 
 [71] "994"  "995"  "407"  "408"  "409"  "412"  "413"  "996"  "997"  "998" 
 [81] "999"  "488"  "489"  "569"  "789"  "1351" "1885" "1003" "1004" "1015"
 [91] "1910" "12"   "1555" "1579" "1354" "1353" "17"   "1016" "742"  "1017"
[101] "805"  "1018" "806"  "1019" "1475" "1020" "1021" "1022" "1023" "505" 
[111] "690"  "1487" "138"  "139"  "140"  "141"  "142"  "143"  "771"  "144" 
[121] "145"  "163"  "164"  "165"  "1361" "1589" "1884" "1560" "166"  "167" 
[131] "169"  "170"  "171"  "172"  "807"  "1878" "2148" "2197" "2245" "2223"
[141] "1976" "1975" "2063" "2068" "2076" "1922" "2010" "568"  "2198" "808"

In [ ]:
# 412, 996, 742

In [118]:
which(bus_stops_r4_dir1_post == '742', arr.ind = T)

[1] 99

In [119]:
for(i in bus_stops_r4_dir1_post[100:length(bus_stops_r4_dir1_post)]){
    print(i)
    RF_Ferns_and_Ranger('4', '1', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "1017"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "805"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "1018"


...

[1] "Done!"
[1] "_/|_/|_"
[1] "2198"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "808"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)


Warning message:
“Unknown or uninitialised column: `board_count`.”


[1] "Done!"
[1] "_/|_/|_"


## Route 9 

### Direction 0

#### Pre-lockdown

In [15]:
bus_stops_r9_dir0_pre

[1]  354  505  784  283  284  285  713  286  287 1351   12 1555 1579 1354 1353
[16]   17  742   19 1557 1357 1499 1084 1085 1086 1087 1088 1089 1090 1091 1092
[31] 1093 1094 1095 1096 1097 1496 1558 1099 1139 1100 1101 1102 1103 1104 1105
[46] 1106 1107 1108 1109 1110 1111 1112 1113 1114 1115 1116 1117 1118 1119 1120
[61] 1121 1122 1123 1124 1125 1126 1127 1128 1129 1130 1131 1132 1133 1134 1498
[76] 1559 1136 1710 1224

In [ ]:
# 285, 287, 1087

In [125]:
which(bus_stops_r9_dir0_pre == '1087', arr.ind = T)

[1] 25

In [126]:
for(i in bus_stops_r9_dir0_pre[26:length(bus_stops_r9_dir0_pre)]){
    print(i)
    RF_Ferns_and_Ranger('9', '0', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "1088"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

344 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 276, 275, 275, 275, 275, 274, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9273000  0.6454373
   2     0.8998465  0.5835320
   3     0.8970722  0.5708391
   5     0.9287486  0.6470722
   6     0.9171331  0.6085414
   7     0.9127421  0.5980121
   9     0.9098228  0.5876343
  10     0.9012307  0.5637042
  11     0.9026391  0.5699501
  13     0.8924303  0.5421786
  14     0.8693862  0.4910166
  15     0.8807520  0.5113607

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 5.


Warning message in train.default(x, y, weights = w, ...):
“You are trying to do regression and your outcome only has two possible values Are you trying to do classification? If so, use a 2 level factor as your outcome column.”
Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

26 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 21, 21, 21, 20, 21, 21, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared   MAE      
   1             15    extratrees  0.3636102  0.3353588  0.2659084
   1             28    maxstat     0.3651241  0.3089931  0.2763125
   2             22    variance    0.3570058  0.3181069  0.2573872
   2             33    variance    0.3641895  0.3095165  0.2564155
   5              2    maxstat     0.3816217  0.3753582  0.3139703
   5             18    variance    0.3539271  0.3388379  0.2562443
   5             24    variance    0.3570998  0.3200773  0.2558056
   7             25    extratrees  0.3607086  0.3347127  0.2634664
   7             25    variance    0.3574906  0.3329945  0.2571441
   9              6    variance    0.3569020  0.3571188  0.2730510
   9             32    maxstat     0.3673012  0.

...

Random Ferns 

1053 samples
   7 predictor
   2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 842, 843, 843, 841, 843, 843, ... 
Resampling results across tuning parameters:

  depth  Accuracy     Kappa
   1     0.003796025  0    
   2     0.001891264  0    
   3     0.001891264  0    
   5     0.001891264  0    
   6     0.001891264  0    
   7     0.001891264  0    
   9     0.001891264  0    
  10     0.001891264  0    
  11     0.001891264  0    
  13     0.001891264  0    
  14     0.001891264  0    
  15     0.001891264  0    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.


Warning message in confusionMatrix.default(y_clf_test, rf_random_pred):
“Levels are not in the same order for reference and data. Refactoring data to match.”
Warning message in train.default(x, y, weights = w, ...):
“You are trying to do regression and your outcome only has two possible values Are you trying to do classification? If so, use a 2 level factor as your outcome column.”
Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

2 samples
7 predictors

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1, 1, 1, 1 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE  Rsquared  MAE
  1              10    maxstat     2     NaN       2  
  1              14    maxstat     2     NaN       2  
  1              15    extratrees  2     NaN       2  
  1              20    extratrees  2     NaN       2  
  1              20    maxstat     2     NaN       2  
  1              21    extratrees  2     NaN       2  
  1              23    extratrees  2     NaN       2  
  1              24    variance    2     NaN       2  
  1              25    extratrees  2     NaN       2  
  1              25    variance    2     NaN       2  
  1              28    maxstat     2     NaN       2  
  1              32    variance    2     NaN       2  
  1              33    extratrees  2     NaN       2  
  2               6    maxstat   


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

1311 samples
   7 predictor
   2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 1050, 1049, 1048, 1048, 1049, 1050, ... 
Resampling results across tuning parameters:

  depth  Accuracy  Kappa
   1     1         1    
   2     1         1    
   3     1         1    
   5     1         1    
   6     1         1    
   7     1         1    
   9     1         1    
  10     1         1    
  11     1         1    
  13     1         1    
  14     1         1    
  15     1         1    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

518 samples
  7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 414, 415, 414, 414, 415, 415, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared     MAE      
   1   

In [127]:
#### Post-lockdown

In [128]:
bus_stops_r9_dir0_post

[1] "354"  "505"  "784"  "283"  "284"  "285"  "713"  "286"  "287"  "1351"
[11] "12"   "1555" "1579" "1354" "1353" "17"   "742"  "19"   "1557" "1357"
[21] "1499" "1084" "1085" "1086" "1087" "1088" "1089" "1090" "1091" "1092"
[31] "1093" "1094" "1095" "1096" "1097" "1496" "1558" "1099" "1139" "1100"
[41] "1101" "1102" "1103" "1104" "1105" "1106" "1107" "1108" "1109" "1110"
[51] "1111" "1112" "1113" "1224" "1115" "1116" "1117" "1118" "1119" "1120"
[61] "1121" "1122" "1123" "1124" "1125" "1126" "1127" "1128" "1129" "1130"
[71] "1131" "1132" "1133" "1134" "1498" "1559" "1136" "1710"

In [ ]:
# 1087, 1096, 1104, 1559

In [136]:
which(bus_stops_r9_dir0_post == '1559', arr.ind = T)

[1] 76

In [137]:
for(i in bus_stops_r9_dir0_post[77:length(bus_stops_r9_dir0_post)]){
    print(i)
    RF_Ferns_and_Ranger('9', '0', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "1136"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

168 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 135, 134, 135, 134, 134, 134, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.9401070  0.8537293
   2     0.9164884  0.7957759
   3     0.9223708  0.8132687
   5     0.9016934  0.7678710
   6     0.9048128  0.7764548
   7     0.9134581  0.7896082
   9     0.8959002  0.7536162
  10     0.8869875  0.7353421
  11     0.8752228  0.7155066
  13     0.8693405  0.7026820
  14     0.8722816  0.7070518
  15     0.8512478  0.6688679

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

38 samples
 7 predictor

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 31, 30, 30, 31, 30, 30, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  split


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


## Route 9 

### Direction 1

#### Pre-lockdown

In [138]:
bus_stops_r9_dir1_pre

[1] "1710" "1701" "1706" "1707" "1708" "1142" "1143" "1144" "1145" "1146"
[11] "1147" "1501" "1148" "1149" "1150" "1151" "1152" "1153" "1154" "1155"
[21] "1156" "1157" "1502" "1159" "1161" "1162" "1163" "1164" "1548" "1503"
[31] "1556" "1168" "1169" "1171" "1172" "1173" "1174" "1175" "1504" "1177"
[41] "1178" "1179" "1180" "1181" "1505" "1183" "1184" "1185" "1186" "1187"
[51] "1188" "1189" "1190" "1191" "1192" "1193" "1461" "142"  "143"  "771" 
[61] "144"  "145"  "1560" "163"  "164"  "165"  "1361" "1589" "166"  "167" 
[71] "169"  "170"  "171"  "172"  "505"  "690"

In [ ]:
# 1189, 169, 170, 171, 172

In [143]:
which(bus_stops_r9_dir1_pre == '169', arr.ind = T)

[1] 71

In [147]:
for(i in bus_stops_r9_dir1_pre[75:length(bus_stops_r9_dir1_pre)]){
    print(i)
    RF_Ferns_and_Ranger('9', '1', i, 'pre')
    print('Done!')
    print('_/|_/|_')
}

[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

166 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 133, 134, 132, 132, 133, 132, ... 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa     
   1     0.6806874  0.12889302
   2     0.6270332  0.09267451
   3     0.6264817  0.11385113
   5     0.5878064  0.07987615
   6     0.5669452  0.09937578
   7     0.5191734  0.07697015
   9     0.4502562  0.05824889
  10     0.4011976  0.04926621
  11     0.3686720  0.04041165
  13     0.2684436  0.02407236
  14     0.2294953  0.01866695
  15     0.1841967  0.01325981

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.


Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

7 samples
7 predictors

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 6, 6, 6, 5, 5, 6, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared  MAE     
  1               5    variance    4.382544    1       3.969445
  1               6    extratrees  4.339128    1       3.919583
  1              12    maxstat     4.734111    1       4.311317
  2               2    extratrees  5.023405    1       4.587912
  2               9    maxstat     4.680824    1       4.239165
  2              10    extratrees  4.390843    1       3.977173
  2              20    extratrees  4.222713    1       3.840977
  3               5    variance    4.742460    1       4.253637
  3              10    extratrees  4.488084    1       4.089223
  3              25    maxstat     4.740822    1       4.351670
  5               1    extratrees  5.307480  NaN       4.843973
  5              15    e


── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"


In [ ]:
#### Post-lockdown

In [148]:
bus_stops_r9_dir1_post

[1] "1710" "1701" "1706" "1707" "1708" "1142" "1143" "1144" "1145" "1146"
[11] "1147" "1501" "1148" "1149" "1150" "1151" "1152" "1153" "1154" "1155"
[21] "1156" "1157" "1502" "1159" "1161" "1162" "1163" "1164" "1548" "1503"
[31] "1556" "1168" "1169" "1171" "1172" "1173" "1174" "1175" "1504" "1177"
[41] "1178" "1179" "1180" "1181" "1505" "1183" "1184" "1185" "1186" "1187"
[51] "1188" "1189" "1190" "1191" "1192" "1193" "1461" "142"  "143"  "771" 
[61] "144"  "145"  "1560" "163"  "164"  "165"  "1361" "1589" "166"  "167" 
[71] "169"  "170"  "171"  "172"  "505"  "690"

In [45]:
# 1143, 1187, 1189, 1192

In [156]:
which(bus_stops_r9_dir1_post == '1192', arr.ind = T)

[1] 55

In [157]:
for(i in bus_stops_r9_dir1_post[56:length(bus_stops_r9_dir1_post)]){
    print(i)
    RF_Ferns_and_Ranger('9', '1', i, 'post')
    print('Done!')
    print('_/|_/|_')
}

[1] "1193"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




Random Ferns 

120 samples
  7 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 96, 96, 96, 96, 96, 96, ... 
Resampling results across tuning parameters:

  depth  Accuracy    Kappa
   1     0.02483333  0    
   2     0.02483333  0    
   3     0.02483333  0    
   5     0.02483333  0    
   6     0.02483333  0    
   7     0.02483333  0    
   9     0.02483333  0    
  10     0.02483333  0    
  11     0.02483333  0    
  13     0.02483333  0    
  14     0.02483333  0    
  15     0.02483333  0    

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.


Warning message in confusionMatrix.default(y_clf_test, rf_random_pred):
“Levels are not in the same order for reference and data. Refactoring data to match.”
Warning message in train.default(x, y, weights = w, ...):
“You are trying to do regression and your outcome only has two possible values Are you trying to do classification? If so, use a 2 level factor as your outcome column.”
Warning message in nominalTrainWorkflow(x = x, y = y, wts = weights, info = trainInfo, :
“There were missing values in resampled performance measures.”


Random Forest 

3 samples
7 predictors

No pre-processing
Resampling: Cross-Validated (5 fold, repeated 2 times) 
Summary of sample sizes: 2, 2, 2, 2, 2, 2, ... 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE       Rsquared  MAE      
  1               1    maxstat     0.6630000  NaN       0.6630000
  1               3    extratrees  0.6776667  NaN       0.6776667
  1               5    variance    0.6736667  NaN       0.6736667
  1              14    extratrees  0.6750000  NaN       0.6750000
  1              20    extratrees  0.6946667  NaN       0.6946667
  2               2    maxstat     0.6760000  NaN       0.6760000
  2               6    extratrees  0.6781667  NaN       0.6781667
  2               9    maxstat     0.6716667  NaN       0.6716667
  2              10    extratrees  0.6576667  NaN       0.6576667
  2              10    variance    0.6698333  NaN       0.6698333
  3               5    variance    0.6753333  NaN       0.6753333


...

[1] "Done!"
[1] "_/|_/|_"
[1] "505"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
[1] "690"



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)



── Column specification ────────────────────────────────────────────────────────
cols(
  month = col_double(),
  service_kind = col_character(),
  hour = col_double(),
  board_count = col_double(),
  mean_precip = col_double(),
  month_average_board_count = col_double(),
  surrounding_board_count = col_double()
)




[1] "Done!"
[1] "_/|_/|_"
